In [1]:
import re
import pandas as pd
from greek_accentuation.characters import *
cmpvbs = {}
df_derivtypes = pd.read_csv('/Users/gcrane/github/morph/pyth/derivtypeinfo.csv')
df_endings = pd.read_csv('/Users/gcrane/github/morph/pyth/endings.csv')
df_vbstemlist = pd.read_csv('/Users/gcrane/github/morph/pyth/vbstemlist.csv')
df_nomstemlist = pd.read_csv('/Users/gcrane/github/morph/pyth/nomstemlist.csv')
df_tbform2lemma = pd.read_csv('/Users/gcrane/github/perstreebanks/nominals_tb',low_memory=False)
df_tbvbform2lemma = pd.read_csv('/Users/gcrane/github/perstreebanks/verbals_tb',low_memory=False)
df_cmpvbs = pd.read_csv('/Users/gcrane/github/perstreebanks/cmpvbs.csv')

In [9]:
import re
from greek_normalisation.utils import (grave_to_acute,strip_last_accent_if_two)


# collect short definitions for vocabulary
lexicalentries = {}
verbarguments = {}
lexfile = "/Users/gcrane/github/Thucydides-new-working-materials/GreekMorphApril18.csv"
with open(lexfile) as f:
    for line in f:

        #print(line)
        #line = line.strip('"')
        fields = line.split(",")
        fields[1] = fields[1].strip('"')
        fields[2] = fields[2].strip('\n')
        fields[2] = fields[2].strip('"')
        lexicalentries[fields[1]] = fields[2]

f.close()

anabasistb = '/Users/gcrane/github/glaux-trees/public/xml/0032-006.xml'
xenmemtb = '/Users/gcrane/github/glaux-trees/public/xml/0032-002.xml'
#hellenicatb = '/Users/gcrane/github/glaux-trees/public/xml/0032-001.xml'
republictb = '/Users/gcrane/github/glaux-trees/public/xml/0059-030.xml'
#iliadtb = '/Users/gcrane/github/gAGDT/data/xml/tlg0012.tlg001.perseus-grc1.tb.xml'
#thuctb = '/Users/gcrane/github/glaux-trees/public/xml/0003-001.xml'
  
#curtb = republictb
curtb = anabasistb
#curtb = hellenicatb
#curtb = thuctb
#curtb = iliadtb
#curtb = republictb
curtb = xenmemtb
subsetpat = '^[1-7]\.'  # Anab 1 
#subsetpat = '(32[789]|33[01])'

greeksentids = {}
greeksentforms = {}
greeksentlems = {}
greeksentlens = {}
greeksentpostags = {}
greeksentheads = {}
greeksentrels = {}
engsents = {}
engsentcits = {}
engsentlens = {}

greekforms = {}
greeklems = {}
hashead = {}
hasdeps = {}


neutvocsg = 's---nv'
neutnomsg = 's---nn'
neutgensg = 's---ng'
neutdatsg = 's---nd'
neutaccsg = 's---na'

neutvocpl = 'p---nv'
neutnompl = 'p---nn'
neutgenpl = 'p---ng'
neutdatpl = 'p---nd'
neutaccpl = 'p---na'

femvocsg = 's---fv'
femnomsg = 's---fn'
femgensg = 's---fg'
femdatsg = 's---fd'
femaccsg = 's---fa'

femvocpl = 'p---fv'
femnompl = 'p---fn'
femgenpl = 'p---fg'
femdatpl = 'p---fd'
femaccpl = 'p---fa'

mascvocsg = 's---mv'
mascnomsg = 's---mn'
mascgensg = 's---mg'
mascdatsg = 's---md'
mascaccsg = 's---ma'

mascvocpl = 'p---mv'
mascnompl = 'p---mn'
mascgenpl = 'p---mg'
mascdatpl = 'p---md'
mascaccpl = 'p---ma'

commvocsg = 's---cv'
commnomsg = 's---cn'
commgensg = 's---cg'
commdatsg = 's---cd'
commaccsg = 's---ca'

commvocpl = 'p---cv'
commnompl = 'p---cn'
commgenpl = 'p---cg'
commdatpl = 'p---cd'
commaccpl = 'p---ca'


mascparad = [mascnomsg,mascgensg,mascdatsg,mascaccsg,mascnompl,mascgenpl,mascdatpl,mascaccpl]

defart_forms = {
                mascvocsg : 'ὦ', mascnomsg : 'ὁ',  mascgensg : 'τοῦ', mascdatsg :'τῷ',  mascaccsg :'τὸν', 
                mascvocpl : 'ὦ', mascnompl: 'οἱ', mascgenpl : 'τῶν',mascdatpl : 'τοῖς', mascaccpl : 'τοὺς',
                femvocsg : 'ὦ', femnomsg : 'ἡ',  femgensg : 'τῆς', femdatsg :'τῇ',  femaccsg :'τὴν', 
                femvocpl : 'ὦ', femnompl: 'αἱ', femgenpl : 'τῶν',femdatpl : 'ταῖς', femaccpl : 'τὰς',
                neutvocsg : 'ὦ', neutnomsg : 'τὸ',  neutgensg : 'τοῦ', neutdatsg :'τῷ',  neutaccsg :'τὸ', 
                neutvocpl : 'ὦ', neutnompl: 'τὰ', neutgenpl : 'τῶν',neutdatpl : 'τοῖς', neutaccpl : 'τὰ',
                commvocsg : 'ὦ', commnomsg : 'ὁ/ἡ/τὸ',  commgensg : 'τοῦ/τῆς', commdatsg :'τῷ/τῇ',  commaccsg :'τὸν/τὴν/τὸ', 
                commvocpl : 'ὦ', commnompl: 'οἱ/αἱ/τὰ', commgenpl : 'τῶν',commdatpl : 'τοῖς/ταῖς', commaccpl : 'τὰ/τὰς/τοὺς'
               }

lemma_pos_forms = {}



def getengsents(fname):
    f = open(fname)
    for l in f:
        l = re.sub('\n','',l)
        l = re.sub('"','',l)
        args = l.split('\t')
        if(not len(args) == 3):
            print('badargs',fname,len(args),l)
            continue
        engsents[args[1]] = args[2]
        engsentcits[args[1]] = args[0]
    
    f.close()
    
def additem(curdict,curitem):
    if(curitem in curdict):
        curdict[curitem] = curdict[curitem] + 1
    else:
        curdict[curitem] = 1
        

getengsents('/Users/gcrane/github/anabasis/sentfile.txt')  

depsdict = {}
formdict = {}
citdict = {}
sentdict = {}
def additem2list(curdict,hasdeps,newdep):
    if(not hasdeps in curdict):
        curdict[hasdeps] = []
    curdict[hasdeps].append(newdep)

def getfeats(curid):
    curform = ''
    if(curid in formdict):
        curform = formdict[curid]
    #print('gf',curid,curform)
    
    curpos = ''
    m = re.search('postag="([^"]+)"',curform)
    if(m):
        curpos = m[1]

    curlemma = ''
    m = re.search('lemma="([^"]+)"',curform)
    if(m):
        curlemma = m[1]

    curhead = ''
    m = re.search('head="([^"]+)"',curform)
    if(m):
        curhead = m[1]

    curinfl = ''
    m = re.search('form="([^"]+)"',curform)
    if(m):
        curinfl = m[1]

    currel = ''
    m = re.search('relation="([^"]+)"',curform)
    if(m):
        currel = m[1]
    return(curpos,curlemma,curinfl,curhead,currel)


def getgreeksents(fname):
    f = open(fname)
    cursent = ''
    i = 0
    for l in f:
        l = re.sub('\n','',l)
        m = re.search('<sentence id="([0-9]+)"',l)
        if(m):
            if(cursent):
                i = i + 1
                #if(i<100):
                #    print(l)
                #    print(' '.join(greeksentforms[cursent]))
            cursent = m[1]
            greeksentforms[cursent] = []
            greeksentlems[cursent] = []
            greeksentpostags[cursent] = []
            greeksentrels[cursent] = []
        m = re.search('subdoc="([^"]+)"',l)
        if(m):
            curcit = m[1]
        m = re.search('word id="([^"]+)',l)
        if(m):
            
            curid = m[1]
            formdict[curid] = l
            curpostag,curlemma,curform,curhead,currel = getfeats(curid)
            #curform = m[2]
            #curlemma = m[3]
            #curpostag = m[4]
            #curhead = m[5]
            #currel = m[6]
            #print('a',curid,curlemma)
            hashead[curid] = curhead
            if(curhead in hasdeps):
                hasdeps[curhead].append(curid)
            else:
                hasdeps[curhead] = [curid]
            
            if(not curlemma in lemma_pos_forms):
                lemma_pos_forms[curlemma] = {}
            additem(lemma_pos_forms[curlemma], curpostag + ':' + strip_last_accent_if_two(grave_to_acute(curform)))
            
            greeksentforms[cursent].append(curform)
            additem(greekforms,curform)
            greeksentlems[cursent].append(curlemma)
            additem(greeklems,curlemma)
            greeksentpostags[cursent].append(curpostag)
            greeksentrels[cursent].append(currel)
            if(not curhead == '0'):
                additem2list(depsdict,curhead,curid)
            citdict[curid] = curcit
    f.close()
    print(fname,'len',len(lemma_pos_forms))
    for foo in greeksentlems:
        greeksentlens[foo] = len(greeksentlems[foo])

def get_relation(l):
    m = re.search('relation="([^"]+)"',l)
    if(m):
        return(m[1])
    else:
        return('')
    
def get_postag(l):
    m = re.search('postag="([^"]+)"',l)
    if(m):
        return(m[1])
    else:
        return('')
    
def get_lemma(l):
    m = re.search('lemma="([^"]+)"',l)
    if(m):
        return(m[1])
    else:
        return('')

def get_curid(l):
    m = re.search('id="([^"]+)"',l)
    if(m):
        return(m[1])
    else:
        return('')

def is_decl1(curlemma):
    if(re.search('(ος|ός)$',curlemma)):
        return(1)
    return(0)

def has_matchingarticle(headid,matchpos):
    rlist = []
    if( not headid in depsdict):
        return
    for foo in depsdict[headid]:
        l = formdict[foo]
        if(re.search('lemma="ὁ"',l) and re.search('relation="ATR',l) and re.search(matchpos,l)):
            rlist.append(get_curid(l))
    return(rlist)
 
def intersection(lst1, lst2):
    return list(set(lst1) & set(lst2))

fname = curtb
print(fname)

getgreeksents(curtb)
sword = 'στρατηγός'
sword = 'ἔχει'
sword = 'Δαρεικός'
sword = 'ἦν'
sword = 'ἦσαν'
sword = 'ἔχει'
sword = 'πέμπουσι'
sword = 'στρατηγός'
sword = 'ἀδελφός'
sword = 'ποταμός'
sword = 'κώμη'


/Users/gcrane/github/glaux-trees/public/xml/0032-002.xml
/Users/gcrane/github/glaux-trees/public/xml/0032-002.xml len 2807


In [3]:
i = 0

for foo in greeklems:
    if(i>10):
        continue
    i = i + 1
        
    dfstems = df_nomstemlist[df_nomstemlist.lemma==foo]

    print(foo,dfstems)

πολλάκις        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
34985       34985    πολλακι         pollaki   πολλάκι       polla/ki   
34986       34986   πολλακις        pollakis  πολλάκις      polla/kis   

          lemma lemma_beta formstatus stemtype steminfo genders numbers cases  \
34985  πολλάκις  polla/kis   fullform   adverb   indecl      na      na    na   
34986  πολλάκις  polla/kis   fullform   adverb   indecl      na      na    na   

      degrees dialects enclitic misc  
34985      na     epic       na   na  
34986      na       na       na   na  
θαυμάζω Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: []
τίς        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta lemma  \
35625       35625         τα              ta        τά            ta/   τίς   
35722       35722     τεο

καθηδυπαθέω Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: []
σύ        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta lemma  \
35329       35329         σε              se        σε             se    σύ   
35330       35330         σε              se        σέ            se/    σύ   
35369       35369       σειο            seio      σεῖο          sei=o    σύ   
35370       35370        σεο             seo       σεο            seo    σύ   
35371       35371        σεο             seo       σέο           se/o    σύ   
35372       35372      σεθεν           seqen     σέθεν         se/qen    σύ   
35377       35377        σευ             seu       σευ            seu    σύ   
35378       35378        σευ             seu       σεῦ           seu=    σύ   
35431       35431        σφω             sfw       σφώ     

ἵνα        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta lemma  \
33162       33162        ἱνα            i(na       ἵνα          i(/na   ἵνα   
33163       33163        ἱνα            i(na       ἵνα          i(/na   ἵνα   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
33162      i(/na   fullform   adverb   indecl      na      na    na      na   
33163      i(/na   fullform     conj   indecl      na      na    na      na   

      dialects enclitic misc  
33162       na       na   na  
33163       na       na   na  
εὖ        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta lemma  \
32735       32735         ἐυ             e)u        ἐΰ          e)u/+    εὖ   
32817       32817         εὐ             eu)        εὖ           eu)=    εὖ   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
32735       eu)=   fullform   adverb   indecl      na      na    na      na   
32817       eu)=   fullform 

θαρσέω Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: []
προσέρχομαι Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: []
ὥσπερ        Unnamed: 0 stemnodiac stemnodiac_beta  stemwdiac stemwdiac_beta  lemma  \
36457       36457      ὡσπερ          w(sper      ὥσπερ        w(/sper  ὥσπερ   
36458       36458  ὡσπερανει      w(speranei  ὡσπερανεί    w(speranei/  ὥσπερ   
36459       36459    ὡσπερει        w(sperei    ὡσπερεί      w(sperei/  ὥσπερ   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
36457    w(/sper   fullform   adverb   indecl      na      na    na      na   
36458    w(/sper   fullform   adverb   indecl      na      na 

ἀνίστημι Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: []
ἐγκέλευστος        Unnamed: 0 stemnodiac stemnodiac_beta  stemwdiac stemwdiac_beta  \
57814       57814  ἐγκελευστ      e)gkeleust  ἐγκελευστ     e)gkeleust   

             lemma     lemma_beta formstatus stemtype steminfo genders  \
57814  ἐγκέλευστος  e)gke/leustos    rawstem    os_on     adj2      na   

      numbers cases degrees dialects enclitic misc  
57814      na    na      na       na       na   na  
οἷος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta lemma  \
88292       88292         οἱ             oi(        οἱ            oi(  οἷος   
88293       88293         οἱ             oi(        οἱ            oi(  οἷος   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
88292     oi(=os    rawstem  os_h_on  

...

ἔντονος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
60060       60060      ἐντον          e)nton     ἐντον         e)nton   

         lemma lemma_beta formstatus stemtype steminfo genders numbers cases  \
60060  ἔντονος  e)/ntonos    rawstem    os_on     adj2      na      na    na   

      degrees dialects enclitic misc  
60060      na       na       na   na  
Γάνος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  lemma  \
14167       14167        Γαν            *gan       Γαν           *gan  Γάνος   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
14167    *ga/nos    rawstem    os_ou    noun2    masc      na    na      na   

      dialects enclitic misc  
14167       na       na   na  
Νέος Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: [

ἐναντίον        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
32502       32502   ἐναντιον       e)nantion  ἐναντίον     e)nanti/on   

          lemma  lemma_beta formstatus stemtype steminfo genders numbers  \
32502  ἐναντίον  e)nanti/on   fullform   adverb   indecl      na      na   

      cases degrees dialects enclitic misc  
32502    na      na       na       na   na  
ἀγνώμων        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
38705       38705      ἀγνωμ          a)gnwm     ἀγνωμ         a)gnwm   

         lemma lemma_beta formstatus stemtype steminfo genders numbers cases  \
38705  ἀγνώμων  a)gnw/mwn    rawstem    wn_on     adj3      na      na    na   

      degrees dialects enclitic misc  
38705      na       na       na   na  
ἐνστρατοπεδεύω Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enc

ἄτιμος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta   lemma  \
47859       47859       ἀτιμ           a)tim      ἀτῑμ         a)ti_m  ἄτιμος   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
47859   a)/timos    rawstem    os_on     adj2      na      na    na      na   

      dialects enclitic misc  
47859       na       na   na  
ἀνύω Empty DataFrame
Columns: [Unnamed: 0, stemnodiac, stemnodiac_beta, stemwdiac, stemwdiac_beta, lemma, lemma_beta, formstatus, stemtype, steminfo, genders, numbers, cases, degrees, dialects, enclitic, misc]
Index: []
ἀπειλή        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta   lemma  \
44357       44357      ἀπειλ          a)peil     ἀπειλ         a)peil  ἀπειλή   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
44357   a)peilh/    rawstem     h_hs    noun1     fem      na    na      na   

      dialects enclitic      misc  
44357       na       na 

Λαμψακηνός        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
18124       18124   Λαμψακην       *lamyakhn  Λαμψακην      *lamyakhn   

            lemma    lemma_beta formstatus stemtype steminfo genders numbers  \
18124  Λαμψακηνός  *lamyakhno/s    rawstem  os_h_on     adj1      na      na   

      cases degrees dialects enclitic      misc  
18124    na      na       na       na  suff_acc  
ἐμπόδιος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
59274       59274     ἐμποδι         e)mpodi    ἐμποδι        e)mpodi   

          lemma  lemma_beta formstatus stemtype steminfo genders numbers  \
59274  ἐμπόδιος  e)mpo/dios    rawstem    os_on     adj2      na      na   

      cases degrees dialects enclitic misc  
59274    na      na       na       na   na  
μειλίχιος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
81152       81152    μειλιχι         meilixi   μειλιχι        meilixi   

           lemma  lemma_b

γήινος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta   lemma  \
68272       68272        γηι             ghi       γηϊ           ghi+  γήινος   
68274       68274       γηιν            ghin      γηϊν          ghi+n  γήινος   

      lemma_beta formstatus stemtype steminfo genders numbers cases degrees  \
68272    gh/inos    rawstem    os_ou    noun2    masc      na    na      na   
68274    gh/inos    rawstem  os_h_on     adj1      na      na    na      na   

      dialects enclitic misc  
68272       na       na   na  
68274       na       na   na  
βουπόρος        Unnamed: 0 stemnodiac stemnodiac_beta stemwdiac stemwdiac_beta  \
50785       50785     βουπορ          boupor    βουπορ         boupor   

          lemma lemma_beta formstatus stemtype steminfo genders numbers cases  \
50785  βουπόρος  boupo/ros    rawstem    os_on     adj2      na      na    na   

      degrees dialects enclitic      misc  
50785      na       na       na  stem_acc  
ὀβελίσκος  

In [4]:
optatives = []
perfects = []
aoristpass = []
comparatives = []
superlatives = []
mediopassives = []
miverbs = []
genabsolutes = []
allverbs = {}
totforms = 0

preplist = {}
prepusages = []
prep_acc = {}
prep_gen = {}
prep_dat = {}

outfname = 'tbankout.txt'
def prepdep(curid,curhead):
    #print(curid,curhead)
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(headlemma == '(καί|,)' or re.search('^[bu]',headpos)):
        #print('kai')
        curhead = headhead
        headpos,headlemma,headform,headhead,headrel = getfeats(curhead)

    if(curlemma == '(καί|,)' or re.search('^[bu]',curpos)):
        return

    if(re.search('^r',headpos)):
        m = re.search('([a-z].)$',curpos)
        if(m):
            curcase = m[1]
        else:
            curcase = 'x'
        #print(headlemma,curcase,curform,curlemma,curpos,citdict[curid])
        additem(preplist,headlemma)
        prepusages.append([headlemma,curcase,curform,curlemma,curpos,citdict[curid]])
        if(curcase[0] == 'a'):
            additem(prep_acc,headlemma)
        elif(curcase[0] == 'g'):
            additem(prep_gen,headlemma)
        elif(curcase[0] == 'd'):
            additem(prep_dat,headlemma)
noungennouns = []

def getnoungennouns(curid):
    global noungennouns
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('^n.+g-$',curpos) and currel == 'ATR' and re.search('^[pn]',headpos)):
        noungennouns.append([len(noungennouns)+1,curform,currel,headform,headlemma,curid,citdict[curid]])
        #print('ngn',len(noungennouns),curform,currel,headform,headlemma,curid,citdict[curid])

adj2dats = []

def getadj2dats(curid):
    global adj2dats
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('d-$',curpos) and currel == 'ADV' and re.search('^a',headpos)):
        adj2dats.append([len(adj2dats)+1,curform,currel,headform,headlemma,curid,citdict[curid]])
        #print('a2d',len(adj2dats),curform,currel,headform,headlemma,curid,citdict[curid])

multarticles = []
def hasarticle(curid):
    articles = []
    global multarticles
    if(curid == '0' ):
        return


    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    if( curhead == '0'):
        return
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if( headpos and not headpos[0] in ['a','n'] and not re.search('v...p',headpos)):
        return
    for foo in hasdeps[curid]:
        if(foo == '0'):
            continue
        if(re.search('postag="l',formdict[foo])):
            articles.append(foo)
            #return(foo)
            
    if(len(articles)> 1):
        if(not articles in multarticles):
            multarticles.append(articles)
            print('multarticle',len(articles),articles,curid,curform)
        
    return(articles)
            
def autos(curid,curlem):
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    gnc1 = ''
    gnc2 = ''
    m = re.search('^..([sdp])...([mnfc][nvadg])',curpos)
    if(m):
        gnc1 = m[1] + m[2]
        
    m = re.search('^..([sdp])...([mnfc][nvadg])',headpos)
    if(m):
        gnc2 = m[1] + m[2]
    artlist = hasarticle(curhead)
    if(artlist):
        art= artlist[0]
    else:
        art = ''
    #if(curlemma == 'αὐτός' and gnc1 == gnc2):
     #   print('autos2','gnc1='+gnc1,'a'+art,curcit,gnc1,getfeats(curid),gnc2,getfeats(curhead))
    #if(gnc1 and gnc1 == gnc2 and curlemma == 'αὐτός'):
    if(gnc1 and gnc1 == gnc2 and curlemma == curlem):
        if(art):
            artn = int(art)
            autosn = int(curid)
            headn = int(curhead)
            # autos o Kuros
            #return
            if( artn > autosn and artn < headn ):
                print('\nintensive',curcit,formdict[art])
            # o autos  Kuros
            elif( artn < autosn and autosn < headn ):
                print('\nthesame',curcit,formdict[art],artn,autosn,headn)
            else:
                print('\nnocat'+formdict[art])
        #else:
            
        #print('autos1',curid,'art='+art,int(curhead)-int(curid),curlemma,curform,headform,headlemma,curpos,headpos,curcit)

def getattributive(curid):
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    if(curlemma == 'αὐτός'):
        return
    
    if(curhead == 0):
        return
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(not headpos):
        return
    if(curpos[0] == 'r' and headpos[0] in ['a','n']):
        artlist = hasarticle(curhead)
        if(not artlist):
            return
        art = artlist[0]
        artpos,artlemma,artform,arthead,artrel = getfeats(art)
        print(curid,'preponnoun')
        if(art < curid and curid < curhead):
            print('art+prep+noun',curid,artform,curform,headform)
        return
    gnc1 = ''
    gnc2 = ''
    ## this will only find adjectives -- not participles
    m = re.search('^a.([sdp])...([mnfc][nvadg])',curpos)
    if(m):
        gnc1 = m[1] + m[2]
    else:
        return
        
    m = re.search('^[an].([sdp])...([mnfc][nvadg])',headpos)
    if(m):
        gnc2 = m[1] + m[2]
    artlist = hasarticle(curhead)
    art = ''
    if(artlist):
        art = artlist[0]
    if(not art or art == curid):
        return
    
    
    if(not gnc1 == gnc2):
        return
    artpos,artlemma,artform,arthead,artrel = getfeats(art)
    if(art < curid and curid < curhead):
        print('attrib-art+adj+noun',curid,artform,curform,headform)
    elif(curhead < art and  art < curid ):
        print('attrib2-noun+art+adj',curid,headform,artform,curform)
    elif(curid < art and  art < curhead ):
        print('pred1-adj+art+noun',curid,curform,artform,headform)
    else:
        print('pred2-art+adj+noun',curid,artform,curform,headform)

dmeans = 0
datmeansexamp = []

def datmeans(curid):
    global dmeans
    global datmeansexamp
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('d-$',curpos) and currel == 'ADV' and re.search('^v',headpos)):
        dmeans = dmeans + 1
        datmeansexamp.append([curform,currel,headform,curid,citdict[curid]])
        #print('dmeans',dmeans,curform,currel,headform,curid,citdict[curid])
        
iobjverbs = {}       
iobj = 0
def iobjs(curid):
    global iobj
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('d-$',curpos) and currel == 'OBJ' and re.search('^v',headpos)):
        iobj = iobj + 1
        if(not headlemma in iobjverbs):
            iobjverbs[headlemma] = {}
        curdict = iobjverbs[headlemma]
        additem(curdict,curlemma)
        #print('iobj',iobj,curform,currel,headform,headlemma,curid,citdict[curid])

conditionals = {}

def getconditional(curid):
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    headpos2,headlemma2,headform2,headhead2,headrel2 = getfeats(headhead)
    
    
    if(curpos[0] == 'v' and re.search('^(εἰ|ἐάν|ὅταν)$',headlemma)):
        anform2 = 'no-an'
        anlemma2 = 'no-an'
        if(headhead2 in hasdeps):
            for foo in hasdeps[headhead2]:
                deppos,deplemma,depform,dephead,deprel = getfeats(foo)
                if(deplemma == 'ἄν' or deplemma == 'ὅταν'):
                    anform2 = depform
                    anlemma2 = deplemma
        if(not anform2 == 'no-an' or 1):
            print('cond',curcit,curid,curhead,headhead,headform,curform,headform2,anform2)
    
    
gobjverbs = {}       
gobj = 0
def gobjs(curid):
    global gobj
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('g-$',curpos) and currel == 'OBJ' and re.search('^v',headpos)):
        gobj = gobj + 1
        if(not headlemma in gobjverbs):
            gobjverbs[headlemma] = {}
        curdict = gobjverbs[headlemma]
        additem(curdict,curlemma)
        print('gobj',gobj,curform,currel,headform,headlemma,curid,curhead,citdict[curid])

verbarg = 0
def verbargs(curid,curverb,curcase,needrel):
    global verbarg
    subjform = 'nosbj'
    subjlemma = 'nosbj'
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(needrel and not currel == needrel):
        return
    if(re.search(curcase + '-$',curpos) and headlemma == curverb):
        verbarg = verbarg + 1
        for foo in hasdeps[curhead]:
            deppos,deplemma,depform,dephead,deprel = getfeats(foo)
            if(deprel == 'SBJ'):
                subjform = depform
                subjlemma = deplemma
        print('heads',verbarg,curform,currel,headform,headlemma,subjform,subjlemma,curid,citdict[curid])

tempepei = 0
tempcs = ['ἐπεί','ἐπειδή','πρίν']
def tempepeis(curid):
    global tempepei
    subjform = 'nosbj'
    subjlemma = 'nosbj'
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    headpos2,headlemma2,headform2,headhead2,headrel2 = getfeats(headhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    #if(not headrel == 'ADV' or not re.search('^v.+g-$',headpos) or not curpos[0] == 'v'):
    if(not headlemma in tempcs or not re.search('^v',curpos) or not re.search('^v',headpos2)):
        return
    
    else:
        tempepei = tempepei + 1
        if(headhead2 in hasdeps):
            for foo in hasdeps[headhead2]:
                deppos,deplemma,depform,dephead,deprel = getfeats(foo)
                if(deprel == 'SBJ'):
                    subjform = depform
                    subjlemma = deplemma
        print('tempepei',tempepei,headform,headlemma,curform,currel,headform2,headlemma2,headpos2,subjform,subjlemma,curid,citdict[curid])

genagent = 0
def genagents(curid):
    global genagent
    subjform = 'nosbj'
    subjlemma = 'nosbj'
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    headpos2,headlemma2,headform2,headhead2,headrel2 = getfeats(headhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    #if(not headrel == 'ADV' or not re.search('^v.+g-$',headpos) or not curpos[0] == 'v'):
    if(not headlemma == 'ὑπό' or not re.search('g-$',curpos) or not re.search('^v',headpos2)):
        return
    
    else:
        genagent = genagent + 1
        if(headhead2 in hasdeps):
            for foo in hasdeps[headhead2]:
                deppos,deplemma,depform,dephead,deprel = getfeats(foo)
                if(deprel == 'SBJ'):
                    subjform = depform
                    subjlemma = deplemma
        print('genagent',genagent,curform,currel,headform,headlemma,headform2,headlemma2,headpos2,subjform,subjlemma,curid,citdict[curid])



purpclause = 0
purpclausconjs = ['ἵνα','ὡς','ὅπως']
primarytenses = ['p','f','r','t']
secondarytenses = ['i','a','l']
def purpclauses(curid):
    global purpclause
    subjform = 'nosbj'
    subjlemma = 'nosbj'
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    headpos2,headlemma2,headform2,headhead2,headrel2 = getfeats(headhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    #if(not headrel == 'ADV' or not re.search('^v.+g-$',headpos) or not curpos[0] == 'v'):
    if(not headlemma in purpclausconjs or not re.search('^v...[so]',curpos) or not re.search('^v',headpos2)):
        return
    
    else:
        purpclause = purpclause + 1
        if(headhead2 in hasdeps):
            for foo in hasdeps[headhead2]:
                deppos,deplemma,depform,dephead,deprel = getfeats(foo)
                if(deprel == 'SBJ'):
                    subjform = depform
                    subjlemma = deplemma
        curtag = 'other' + headpos2[3] + curpos[4]
        if(headpos2[3] in primarytenses and curpos[4] == 's'):
            curtag = 'primary'
        elif(headpos2[3] in secondarytenses and curpos[4] == 'o'):
            curtag = 'secondary'
        elif(headpos2[3] in secondarytenses and curpos[4] == 's'):
            curtag = 'vivid'
            
        print('purpclause',purpclause,curtag,curform,currel,headform,headlemma,headform2,headlemma2,headpos2,subjform,subjlemma,curid,citdict[curid])


futpart = 0
def futparts(curid):
    global futpart
    subjform = 'nosbj'
    subjlemma = 'nosbj'
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    if( not re.search('v..fp',curpos)):
        return
    
    else:
        futpart = futpart + 1
        if(headhead in hasdeps):
            for foo in hasdeps[headhead]:
                deppos,deplemma,depform,dephead,deprel = getfeats(foo)
                if(deprel == 'SBJ'):
                    subjform = depform
                    subjlemma = deplemma
        print('futpart',futpart,curform,currel,headform,headlemma,subjform,subjlemma,curid,citdict[curid])

genab = 0
def genabs(curid):
    global genab
    subjform = 'nosbj'
    subjlemma = 'nosbj'
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    #if(not headrel == 'ADV' or not re.search('^v.+g-$',headpos) or not curpos[0] == 'v'):
    if(headrel == 'SBJ'):
        return
    if(not currel == 'ADV' or not re.search('^v.+g-$',curpos) or not re.search('^v',headpos)):
        return
    
    else:
        genab = genab + 1
        if(curid in hasdeps):
            for foo in hasdeps[curid]:
                deppos,deplemma,depform,dephead,deprel = getfeats(foo)
                if(deprel == 'SBJ'):
                    subjform = depform
                    subjlemma = deplemma
        print('genabs',genab,curform,currel,headform,headlemma,subjform,subjlemma,curid,citdict[curid])
        print('genabs',genab,curform,currel,headform,headlemma,subjform,subjlemma,curid,citdict[curid],file=outf)

        
aobjverbs = {} 
exw_objs = {}
aobjnoms = {}
aobj = 0
def aobjs(curid):
    global aobj
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('a-$',curpos) and currel == 'OBJ' and re.search('^v',headpos)):
        aobj = aobj + 1
        if(not headlemma in aobjverbs):
            aobjverbs[headlemma] = {}
        curdict = aobjverbs[headlemma]
        additem(curdict,curlemma)
        
        if(not curlemma in aobjnoms):
            aobjnoms[curlemma] = {}
        curdict = aobjnoms[curlemma]
        additem(curdict,headlemma)
        if(headlemma == 'ἔχω'):
            additem(exw_objs,curlemma)
            #aobjverbs[headlemma] = 1
            print('exw_objs',aobj,curform,currel,headform,headlemma,curid,curhead,citdict[curid])
            
        #print('aobj',aobj,curform,currel,headform,headlemma,curid,citdict[curid])

subj2verbs = {}        
def getsubj2verbs(curid):
    global subj2verbs
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    if(not currel == 'SBJ'):
        return
    if(len(headpos)<5):
        print('shortheadpos',headpos,curhead)
    lemkey = headlemma + '-' + headpos[5]
    if(not curlemma in subj2verbs):
        subj2verbs[curlemma] = {}
    additem(subj2verbs[curlemma],lemkey)
    
    
datobjs = {}
datverbs = {}
def finddatobjs(curid):
    global datobjs
    global datverbs
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(re.search('d-$',curpos) and currel == 'OBJ' and re.search('^v',headpos)):
        if(headlemma in datverbs):
            datverbs[headlemma] = datverbs[headlemma] + 1
        else:
            datverbs[headlemma] = 1
    

datwadjective = []
def finddatwadjective(curid):
    global datpossess
    global tobeverbs
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(re.search('d-$',curpos) and (currel == 'ADV' or currel =='ΑΤΡ') and headpos[0] == 'a' ):
        print('datwadjective',citdict[curid],headform,headlemma,curform)
        datwadjective.append([citdict[curid],headform,headlemma,curform,curid])
    

datpossess = []
tobeverbs = ['εἰμί','γίγνομαι','ὑπάρχω']
def finddatpossess(curid):
    global datpossess
    global tobeverbs
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(re.search('d-$',curpos) and (currel == 'ADV' or currel =='OBJ') and headlemma in tobeverbs):
        print('datposs',curid,citdict[curid],headform,headlemma,curform)
        datpossess.append([citdict[curid],headform,headlemma,curform,curid])
    
neutsubj = []
def findneutsubj(curid):
    global neutsubj
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(re.search('^..p---nn-$',curpos) and (currel =='SBJ') ):
        print('neutsubj2',citdict[curid],headform,headlemma,curform)
        neutsubj.append([citdict[curid],headform,headlemma,curform,curid])
    
doubleobjs = {}
hasobjs = {}
def finddoubleobjs(curid):
    global doubleobjs
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    
    #if(re.search('d-$',curpos) and re.search('ADV',currel) and re.search('^v',headpos)):
    if(re.search('a-$',curpos) and currel == 'OBJ' and re.search('^v',headpos)):
        curkey = curid + ' ' + curform + ' ' + curlemma
        if(curhead in hasobjs):
            hasobjs[curhead].append(curkey)
            #print('multobj',citdict[curid],len(hasobjs[curhead]),headform,headlemma,curhead,hasobjs[curhead])
        else:
            hasobjs[curhead] = [curkey]
            

outf = open(outfname,'w')
for foo in formdict:
    if(not re.search(subsetpat,citdict[foo])):
        continue
        
    curpos,curlemma,curform,curhead,currel = getfeats(foo)
    if(not curpos):
        continue
        #print('nopos',foo,curpos,curform)
    if(curpos[0] == 'v'):
        if(curlemma in allverbs):
            allverbs[curlemma] = allverbs[curlemma] + 1
        else:
            allverbs[curlemma] = 1

    totforms = totforms + 1
    curf = formdict[foo]
        
    if(re.search('"[^"]+g-".+SBJ',curf)):
        genabsolutes.append(curf)
        print('genabs-short',len(genabsolutes),curlemma,curform,curid,citdict[foo])
    if(re.search('"v...o',curf)):
        optatives.append(curf)
    if(re.search('"v..[rl].',curf)):
        perfects.append(curf)
    if(re.search('"v..a.p',curf)):
        aoristpass.append(curf)
    elif(re.search('"v....[pme]',curf)):
        mediopassives.append(curf)
    if(re.search('c" head',curf)):
        comparatives.append(curf)
    if(re.search('lemma="[^"]+μι"',curf)):
        miverbs.append(curf)
    if(re.search('postag="[^"]+s"',curf)):
        superlatives.append(curf)
    m = re.search('head="([^"]+)"',curf)
    if(m):
        curhead = m[1]
    m = re.search('id="([^"]+)"',curf)
    if(m):
        curid = m[1]
    
    prepdep(curid,curhead)
    autos(curid,'πᾶς')
    getattributive(curid)
    datmeans(curid)
    aobjs(curid)
    gobjs(curid)
    iobjs(curid)
    verbargs(curid,'περί','[d]','')
    getnoungennouns(curid)
    getadj2dats(curid)
    finddoubleobjs(curid)
    getsubj2verbs(curid)
    getconditional(curid)
    genabs(curid)
    genagents(curid)
    tempepeis(curid)
    futparts(curid)
    purpclauses(curid)
    finddatobjs(curid)
    finddatpossess(curid)
    findneutsubj(curid)
i = 0
outf.close()
def cntdict(curdict1,curkey):
    if(curkey in curdict1):
        curdict = curdict1[curkey]
    else:
        return(0,0)
    dictlen = len(curdict)
    dicttot = 0
    #print(dictlen,curdict)
    for boo in curdict:
        dicttot = dicttot + curdict[boo]
    return(dictlen,dicttot)

for foo in sorted(allverbs,key=allverbs.get,reverse=True):
    i = i + 1
    dats,dats2 = cntdict(iobjverbs,foo)
    accs,accs2 = cntdict(aobjverbs,foo)
    gens,gens2 = cntdict(gobjverbs,foo)

    
    print(i,allverbs[foo],foo,accs,dats,gens)
#for foo in sorted(preplist):
#    print(foo)
print(totforms)
print('mediopassives',len(optatives))
print('optative',len(optatives))
print('aoristpassive',len(aoristpass))
print('comparatives',len(comparatives))
print('superlatives',len(superlatives))
print('perfects',len(perfects))
print('miverbs',len(miverbs))

   
    

purpclause 1 secondary εἴη OBJ ὡς ὡς ἔπεισαν πείθω v3paia--- nosbj nosbj 8919957 1.1.1
purpclause 2 secondary φαίη OBJ ὡς ὡς διετεθρύλητο διαθρυλέω v3slim--- nosbj nosbj 8920042 1.1.2
genagent 1 ὀρνίθων OBJ ὑπό ὑπό ἀποτρέπεσθαί ἀποτρέπω v--pne--- πλεῖστοί πολύς 8920120 1.1.4
genabs-short 1 δαιμόνιον δαιμονίου 8920158 1.1.4
genabs 1 προσημαίνοντος ADV προηγόρευε προαγορεύω δαιμονίου δαιμόνιον 8920160 1.1.4
genagent 2 θεοῦ OBJ ὑπὸ ὑπό φαινόμενα φαίνω v-pppena- nosbj nosbj 8920200 1.1.5
cond 1.1.5 8920204 8920196 8920190 εἰ ἐφαίνετο ἐδόκει ὅταν
cond 1.1.5 8920215 8920213 8920211 εἰ ἐπίστευεν προέλεγεν no-an
purpclause 3 secondary ἀποβήσοιτο ADV ὅπως ὅπως ἔπεμπεν πέμπω v3siia--- nosbj nosbj 8920263 1.1.6
futpart 1 μαντευσομένους OBJ ἔπεμπεν πέμπω nosbj nosbj 8920264 1.1.6
gobj 1 μαντικῆς OBJ προσδεῖσθαι προσδέω 8920279 8920281 1.1.7
attrib-art+adj+noun 8920295 τῶν τοιούτων ἔργων
neutsubj2 1.1.7 ἐνόμιζεν νομίζω μαθήματα
cond 1.1.8 8920360 8920359 8920344 εἰ συμφέρει καρπώσεται no-an
cond 1.

cond 7.3.11 9052113 9052110 9052117 ἂν ἀνθιστῆται πειρασόμεθα no-an
cond 7.3.13 9052188 9052187 9052177 εἰ δέοι εἴη no-an
genabs 139 ὄντων ADV διατρίβειν διατρίβω ἀγαθῶν ἀγαθός 9052205 7.3.13
genabs-short 134 ἀγαθός ἀγαθῶν 9052205 7.3.13
cond 7.3.13 9052212 9052209 9052215 εἰ προσλήψοιντο ἐδόκει no-an
cond 7.3.14 9052226 9052224 9052228 εἴ ἀντιλέγει λεγέτω no-an
tempepei 314 ἐπεὶ ἐπεί ἀντέλεγεν ADV ἐπεψήφισε ἐπιψηφίζω v3saia--- nosbj nosbj 9052240 7.3.14
exw_objs 2774 κώμην OBJ ἔχων ἔχω 9052276 9052277 7.3.15
tempepei 315 ἐπεὶ ἐπεί ἦσαν ADV ἦν εἰμί v3siia--- nosbj nosbj 9052283 7.3.16
exw_objs 2775 οὕστινας OBJ ἔχειν ἔχω 9052298 9052300 7.3.16
futpart 92 διαπραξόμενοι ADV παρῆσαν πάρειμι nosbj nosbj 9052314 7.3.16
tempepei 316 ἐπεὶ ἐπεί εἴληφεν ADV ἔσοιτο εἰμί v3sfom--- Μήδοκος Μήδοκος 9052347 7.3.16
cond 7.3.17 9052368 9052366 9052371 ἢν σωφρονῆτε δώσετε no-an
cond 7.3.17 9052386 9052381 9052380 ἐὰν διδῶτε ἢ no-an
tempepei 317 ἐπεὶ ἐπεί ἤκουσεν ADV ἔλεγεν λέγω v3siia--- nosbj nosbj 90

cond 7.6.12 9055988 9055987 9055984 εἰ πείσαιμι ὑπισχνουμένου no-an
neutsubj2 7.6.12 εἶναι εἰμί ταῦτα
tempepei 337 ἐπεὶ ἐπεί ἐκώλυε ADV συνέλεξα λέγω v1saia--- nosbj nosbj 9056035 7.6.13
purpclause 128 secondary βουλευσαίμεθα ADV ὅπως ὅπως συνέλεξα λέγω v1saia--- nosbj nosbj 9056051 7.6.13
gobj 290 Ἀριστάρχου OBJ ἀκούοντες ἀκούω 9056061 9056059 7.6.14
gobj 291 Σεύθου OBJ ἀκούοντες ἀκούω 9056070 9056068 7.6.14
tempepei 338 ἐπεί ἐπεί ἤρξατο ADV αἰτιῷσθε αἰτιάομαι v2ppoe--- nosbj nosbj 9056103 7.6.15
cond 7.6.15 9056111 9056109 9056118 εἰ ἐπαινῶ αἰτιῷσθε no-an
cond 7.6.15 9056133 9056122 9056146 εἰ εἰμι ἔχοιμι no-an
genagent 77 ὑμῶν OBJ ὑφ’ ὑπό αἱρούμενος αἱρέω v-sppemn- nosbj nosbj 9056144 7.6.15
exw_objs 2984 αἰτίαν OBJ ἔχοιμι ἔχω 9056145 9056146 7.6.15
exw_objs 2985 ὑμέτερα OBJ ἔχοντα ἔχω 9056160 9056161 7.6.16
gobj 292 ὧν OBJ δοίη δίδωμι 9056183 9056186 7.6.16
cond 7.6.16 9056197 9056196 9056202 εἰ ἐδίδου ἐδίδου no-an
cond 7.6.17 9056217 9056213 9056219 εἰ οἴεσθε ἔξεστιν no-an
cond 7.

cond 7.7.30 9058732 9058731 9058699 εἰ καταδοξάσειαν μένοντας no-an
genagent 88 σοῦ OBJ ὑπὸ ὑπό ἀδικεῖσθαι ἀδικέω v--pne--- οἳ ὅς 9058780 7.7.31
cond 7.7.31 9058794 9058790 9058772 ἐὰν ὑπισχνῶνται λάβωσι no-an
cond 7.7.31 9058804 9058799 9058797 ἂν ἀναπράξωσιν συστρατεύσεσθαι no-an
gobj 303 στρατιᾶς OBJ δεῖσθαι δέω 9058813 9058811 7.7.31
genabs-short 145 σύ σοῦ 9058838 7.7.32
genabs 152 κρατοῦντος ADV ὑπάρχει ὑπάρχω σοῦ σύ 9058842 7.7.32
datposs 9058845 7.7.32 ὑπάρχει ὑπάρχω αὐτοῖς
genabs-short 146 σύ σου 9058848 7.7.32
gobj 304 χώρας OBJ προνοεῖσθαι προνοέω 9058856 9058857 7.7.33
cond 7.7.33 9058860 9058852 9058867 εἰ δεῖ οἴει no-an
genabs 153 οὔσης ADV δεῖ δεῖ nosbj nosbj 9058863 7.7.33
cond 7.7.33 9058883 9058874 9058872 εἰ οἴχοιντο εἶναι ἂν
cond 7.7.33 9058889 9058886 9058883 εἰ μένοιεν οἴχοιντο no-an
gobj 305 ἐπιτηδείων OBJ δεομένους δέω 9058903 9058901 7.7.33
cond 7.7.34 9058916 9058912 9058910 εἰ ἀποδοθείη ἀναλωθείη no-an
cond 7.7.34 9058922 9058919 9058916 εἰ ὀφείλοιντο ἀποδοθε

271 8 ὀπισθοφυλακέω 1 0 0
272 8 ἀπαντάω 0 4 0
273 8 ἐνθυμέομαι 1 0 0
274 8 ἀρκέω 1 2 0
275 8 ἀναμιμνῄσκω 3 0 0
276 8 ὑφίστημι 1 1 1
277 8 παρίημι 0 2 0
278 8 καταμένω 2 1 0
279 7 συνέπομαι 1 2 0
280 7 ἀέκων 0 0 0
281 7 χρῄζω 1 1 0
282 7 χωρέω 2 0 0
283 7 ἐσθίω 4 0 0
284 7 διασπάω 0 0 0
285 7 προσήκω 0 2 0
286 7 ἀνέχω 2 0 0
287 7 παρακελεύομαι 0 5 0
288 7 πίπτω 0 0 0
289 7 συντίθημι 3 2 0
290 7 ἀποτέμνω 1 0 1
291 7 ἀναλαμβάνω 6 0 0
292 7 παρατάσσω 0 0 0
293 7 προπέμπω 4 1 0
294 7 ἐμπίπτω 0 3 0
295 7 ἐπιορκέω 2 0 0
296 7 ἀγωνίζομαι 1 0 0
297 7 διάκειμαι 0 2 0
298 7 στασιάζω 0 1 0
299 7 ἀνατείνω 1 0 0
300 7 διαφθείρω 5 0 1
301 7 παράγω 3 1 0
302 7 διαβιβάζω 3 0 0
303 7 ὑπερβάλλω 3 0 0
304 7 ἐπίκειμαι 1 2 0
305 7 παραπλέω 1 0 0
306 7 ὀρχέομαι 2 0 0
307 7 σωφρονέω 1 0 0
308 7 δωρέω 3 3 0
309 6 βασιλεύω 1 0 1
310 6 διατίθημι 4 0 0
311 6 ἐκβάλλω 4 1 0
312 6 συμπράσσω 2 2 0
313 6 δαπανάω 1 0 0
314 6 θεωρέω 4 0 0
315 6 προβάλλω 3 0 0
316 6 ἐκλείπω 3 0 0
317 6 κατακόπτω 2 0 0
318 6 ὑπολείπω 0 0 

716 2 ἀναβάλλω 1 0 0
717 2 διασκηνέω 1 0 0
718 2 παραρρέω 0 1 0
719 2 κατοράω 2 0 0
720 2 ἀνακαλέω 1 0 0
721 2 ἀποκαίω 1 0 0
722 2 πήγνυμι 1 0 0
723 2 ἀποσήπομαι 1 0 0
724 2 τήκω 0 0 0
725 2 κρούω 2 0 0
726 2 παραπέμπω 1 0 0
727 2 ἐξηγέομαι 1 1 0
728 2 εὐωχέω 0 0 0
729 2 ἡβάσκω 0 0 0
730 2 ἐγείρω 0 0 0
731 2 ἀνακομίζω 0 0 0
732 2 περιίστημι 0 1 0
733 2 λοχαγέω 0 1 0
734 2 εἰστρέχω 0 0 0
735 2 χορεύω 0 0 0
736 2 αἴθω 0 0 0
737 2 πατάσσω 1 0 0
738 2 προστατέω 0 0 1
739 2 καλινδέομαι 0 0 0
740 2 ἐκτείνω 1 0 0
741 2 ἀναθορυβέω 0 0 0
742 2 συμπαρασκευάζω 1 0 0
743 2 ὑπερκάθημαι 0 0 1
744 2 ἀποτρέχω 0 0 0
745 2 κατακωλύω 0 0 0
746 2 ἐκτρέχω 1 0 0
747 2 διαφαίνω 0 0 0
748 2 ἐμβιβάζω 1 0 0
749 2 συμμάχομαι 0 2 0
750 2 ἐκτάσσω 0 0 0
751 2 ἐξάρχω 0 0 1
752 2 κατατρέχω 0 0 0
753 2 νέω 0 0 0
754 2 χωρίζω 0 0 0
755 2 ἐπιμένω 0 0 0
756 2 συνήδομαι 0 0 0
757 2 ἀνοίγνυμι 1 0 0
758 2 ἀπειλέω 1 1 0
759 2 ἀναπυνθάνομαι 2 0 0
760 2 καταράομαι 0 1 0
761 2 κατοικίζω 1 0 0
762 2 ἐκπορίζω 2 1 0
763 2 κοινόω 0

1216 1 διαπορέω 0 0 0
1217 1 διακρίνω 0 0 0
1218 1 συνεπιμελέομαι 0 0 1
1219 1 ἀποδέχομαι 0 0 0
1220 1 προκριθάω 0 0 0
1221 1 σιγάζω 1 0 0
1222 1 συνεθέλω 0 0 0
1223 1 ἀπομάχομαι 0 0 0
1224 1 ἐπαπειλέω 0 0 0
1225 1 ἀνασκευάζω 1 0 0
1226 1 ἀθυμόω 0 1 0
1227 1 συμβοάω 1 0 0
1228 1 ἀχθέω 0 0 0
1229 1 περικυκλόω 1 0 0
1230 1 μαχάω 0 0 0
1231 1 μεγαληγορέω 0 0 0
1232 1 ταπεινόω 1 0 0
1233 1 προσεύχομαι 0 1 0
1234 1 ἐξήκω 0 0 0
1235 1 εἰσπλέω 0 0 0
1236 1 πρόκειμαι 0 0 0
1237 1 προσαναλίσκω 1 0 0
1238 1 ποθέω 0 0 0
1239 1 ζημιόω 0 0 0
1240 1 πυρέσσω 0 0 0
1241 1 ἀναθαρσέω 0 0 0
1242 1 συνθεάομαι 1 0 0
1243 1 ἀναφεύγω 0 0 0
1244 1 ἀποταφρεύω 0 0 0
1245 1 ἀποσταυρόω 1 0 0
1246 1 μεσόω 0 0 0
1247 1 ἐπιβοηθέω 0 1 0
1248 1 συνδοκέω 0 1 0
1249 1 προηγέομαι 1 0 0
1250 1 καταχωρίζω 1 0 0
1251 1 προξενέω 1 0 0
1252 1 μεταβάλλω 0 0 0
1253 1 διαπεποράω 0 0 1
1254 1 ἐκμηρύομαι 0 0 0
1255 1 ὑπαντιάζω 0 0 0
1256 1 προαποτρέπομαι 0 0 0
1257 1 προσμένω 1 0 0
1258 1 πολίζω 1 0 0
1259 1 περιτυγχάνω 0 0 0
1260

In [5]:
#exw_objs
def additem(curdict,item):
    if(item in curdict):
        curdict[item] = curdict[item] + 1
    else:
        curdict[item] = 1
        
prepobjs = {}
for foo in prepusages:
    if(not foo[0]=='παρά'):
        continue
    curkey = foo[0]+':'+foo[1]
    if(not curkey in prepobjs):
        prepobjs[curkey] = {}
    additem(prepobjs[curkey],foo[3])
    curprep = foo[0]
    
print(prep_dat[curprep],prep_gen[curprep],prep_acc[curprep])
        
for foo in prepobjs:
    print(foo)
    curdict = prepobjs[foo]
    for boo in sorted(curdict,key=curdict.get,reverse=True):
        print('\t'+boo,curdict[boo])


19 37 12
παρά:g-
	θεός 5
	ὅς 3
	τις 3
	ἐπίσταμαι 2
	πονηρός 2
	χρηστός 2
	οὗτος 2
	ἐγώ 2
	οὐδείς 2
	σύ 1
	ἀρέσκω 1
	ἐκεῖνος 1
	τυγχάνω 1
	αὐτός 1
	σεαυτοῦ 1
	πόλις 1
	ἰατρός 1
	ἄλλος 1
	δύναμαι 1
	τίς 1
	νυκτοθήρας 1
	οἶδα 1
παρά:a-
	νόμος 6
	σημαίνω 2
	δίκαιος 1
	ζῷον 1
	ἀρχή 1
	ἄλλος 1
παρά:d-
	ἄνθρωπος 4
	σύ 4
	ἐγώ 3
	ὕστερος 1
	σύνειμι 1
	αὐτός 1
	θεός 1
	Κεράμων 1
	ἑαυτοῦ 1
παρά:gs
	εὐσεβής 1
παρά:ds
	ἀγαθός 1
	κακός 1


In [6]:
datpossess

[['1.1.9', 'ὦσιν', 'εἰμί', 'οἷς', '8920518'],
 ['1.1.11', 'γίγνεται', 'γίγνομαι', 'ἀνάγκαις', '8920618'],
 ['1.1.14', 'γίγνεσθαί', 'γίγνομαι', 'τοῖς', '8920815'],
 ['1.1.14', 'γενέσθαι', 'γίγνομαι', 'τοῖς', '8920823'],
 ['1.1.15', 'γίγνεται', 'γίγνομαι', 'ἀνάγκαις', '8920874'],
 ['1.2.8', 'ἔσεσθαι', 'εἰμί', 'ἑαυτῷ', '8921514'],
 ['1.2.12', 'γενομένω', 'γίγνομαι', 'Σωκράτει', '8921742'],
 ['1.2.38', 'ἐγεγόνει', 'γίγνομαι', 'Κριτίᾳ', '8923361'],
 ['1.2.59', 'ὄντας', 'εἰμί', 'λόγῳ', '8924664'],
 ['1.2.62', 'ἐστιν', 'εἰμί', 'τούτοις', '8924879'],
 ['1.3.3', 'εἶναι', 'εἰμί', 'αὐτοῖς', '8925214'],
 ['1.4.5', 'ἦν', 'εἰμί', 'ἡμῖν', '8926315'],
 ['1.4.7', 'εἶναι', 'εἰμί', 'μηχανήμασί', '8926548'],
 ['1.6.5', 'ἐστιν', 'εἰμί', 'λαμβάνουσιν', '8927911'],
 ['2.1.26', 'ἐστιν', 'εἰμί', 'σοι', '8931126'],
 ['2.1.33', 'ἔστι', 'εἰμί', 'φίλοις', '8931765'],
 ['2.2.4', 'γένοιτο', 'γίγνομαι', 'ἡμῖν', '8932233'],
 ['2.2.6', 'γένωνται', 'γίγνομαι', 'αὐτοῖς', '8932417'],
 ['2.2.9', 'εἶναί', 'εἰμί', 'σοι', '89

In [53]:
totdatobjs = 0

def verbdeps(curid):
    global totdatobjs
    curcit = citdict[curid]
    curpos,curlemma,curform,curhead,currel = getfeats(curid)
    headpos,headlemma,headform,headhead,headrel = getfeats(curhead)
    if(not curpos[0] == 'v'):
        #print('fail',curform)
        return
    
        
    #print('verb',curpos,curlemma,curform,curhead,currel)
    if(not curid in hasdeps):
        return
    for foo in hasdeps[curid]:
        deppos,deplemma,depform,dephead,deprel = getfeats(foo)
        if(deprel == 'OBJ' and re.search('[agd].$',deppos)):
            totdatobjs = 1 + totdatobjs
            print(totdatobjs,curcit,curid,curlemma,curform,'dep',deplemma,depform,deppos,deprel)

verbtot = 0
curverb = 'ἄχθομαι'
for formid in formdict:
    curpos,curlemma,curform,curhead,currel = getfeats(formid)
    if(not curlemma == curverb):
        continue
    verbtot = verbtot + 1
    verbdeps(formid)
print(verbtot,curverb)

    

5 ἄχθομαι


In [54]:
preplist

{'κατά': 41,
 'ἐπί': 126,
 'διά': 174,
 'ὑπό': 87,
 'πρός': 229,
 'περί': 93,
 'ἐν': 210,
 'παρά': 68,
 'εἰς': 102,
 'ὑπέρ': 15,
 'ἀμφί': 1,
 'νή': 65,
 'ἀπό': 50,
 'μετά': 19,
 'ἄνευ': 23,
 'ἐκ': 82,
 'ἕνεκα': 30,
 'ἕως': 12,
 'σύν': 14,
 'μέχρι': 14,
 'μά': 43,
 'ἀντί': 21,
 'πλησίον': 2,
 'προπάροιθε': 1,
 'πρό': 8,
 'χωρίς': 1,
 'ἔμπροσθεν': 3,
 'ἐναντίον': 1,
 'πέρα': 1}

In [55]:
i = 0
for foo in subj2verbs:
    if(i>10):
        continue
    i = i + 1
    curdict = subj2verbs[foo]
    print('\n',foo)
    for boo in sorted(curdict,key=curdict.get,reverse=True):
        print(curdict[boo],boo)
        
print('datverbs',len(datverbs))

totdatvbs = 0

i = 0
for foo in sorted(datverbs,key=datverbs.get,reverse=True):
    if(i>2):
        continue
    i = i + 1
    print(foo,datverbs[foo])
    totdatvbs = datverbs[foo] + totdatvbs
    
print('forms',totdatvbs)
        


 γράφω
2 εἰμί-a
1 πείθω-a
1 αἰτιάομαι-e

 γραφή
1 εἰμί-a
1 ἀποστερέω-a

 Σωκράτης
78 φημί-a
9 λέγω-a
3 εἰμί-a
2 διδάσκω-a
2 παρέχω-a
2 ποιέω-a
1 ἀδικέω-a
1 ἡγέομαι-e
1 σωφρονέω-a
1 διαφθείρω-a
1 ἐπαγγέλλω-m
1 κρίνω-a
1 ἐπαίρω-m
1 ἀρέσκω-a
1 οἴομαι-e
1 ὠφελέω-a
1 δοκέω-a
1 παύω-a
1 ἐλέγχω-a
1 ἀποκρίνω-m
1 κελεύω-a
1 θαυμάζω-a
1 διασιωπάω-a
1 νομίζω-a
1 ἀποφαίνω-e

 πόλις
2 νομίζω-a
1 οἰκέω-a
1 βούλομαι-e
1 ἀξιόω-a
1 οἴομαι-e
1 κηρύσσω-a
1 ποιέω-a
1 ἐπιμελέομαι-e
1 ἐξετάζω-a
1 ἔχω-a
1 στασιάζω-a
1 ἐπιτρέπω-e
1 εἰμί-m
1 δοκέω-a
1 θαυμάζω-a
1 εἰμί-a
1 λανθάνω-a
1 συνίστημι-a
1 ἀσκέω-a
1 ἀποβλέπω-a
1 προστίθημι-a
1 δημοκρατέομαι-e
1 παύω-m
1 διάγω-a
1 γίγνομαι-e
1 πολιτεύω-p
1 ἡγέομαι-m

 αὐτός
23 εἰμί-a
7 λέγω-a
4 ποιέω-a
4 διαλέγω-p
3 φροντίζω-a
2 ἀμελέω-a
2 σωφρονέω-a
2 διατελέω-a
1 αἰτιάομαι-m
1 βούλομαι-e
1 διαλέγω-e
1 γίγνομαι-e
1 θνῄσκω-a
1 ἐπαινέω-a
1 κατατρίβω-e
1 δέω-e
1 ἐπίσταμαι-e
1 διατίθημι-a
1 ἀφαιρέω-a
1 διδάσκω-a
1 κάθημαι-e
1 ἐξηγέομαι-e
1 ὑπεροράω-a
1 σῴζω-e
1 φυλάσσω-m


In [56]:
import re


tbvoc = {}
tottokens = 0

def addlemma(lem):
    if(lem in tbvoc):
        tbvoc[lem] = tbvoc[lem] + 1
    else:
        tbvoc[lem] = 1
        
def gettbvoc(fname):
    ## limit to the first 69K tokens so we have the same # as in the Anabasis
    limtokens = 69000
    i = 0
    global tottokens
    f = open(fname)
    for l in f:
        if(re.search('postag="u',l)):
            continue
        m = re.search('lemma="([^"]+)"',l)
        if(m):
            i = i + 1
            if(i>limtokens):
                break
            curlem = re.sub('#[0-9]*','',m[1])
            addlemma(curlem)
            tottokens = tottokens + 1
        m = re.search("lemma='([^']+)'",l)
        if(m):
            i = i + 1
            if(i>limtokens):
                break
            curlem = re.sub('#[0-9]*','',m[1])
            addlemma(curlem)
            tottokens = tottokens + 1
    
    f.close()
  
#fname = '/Users/gcrane/github/proiel-treebank/greek-nt.xml'
fname = '/Users/gcrane/github/glaux-trees/public/xml/0011-002.xml'
fname = '/Users/gcrane/github/glaux-trees/public/xml/0003-001.xml'
fname = '/Users/gcrane/github/glaux-trees/public/xml/0032-006.xml'
fname = '/Users/gcrane/github/glaux-trees/public/xml/0032-002.xml'
fname = curtb
fname = republictb
fname = anabasistb



gettbvoc(fname)
print(len(tbvoc))

3687


In [57]:
import re
from greek_accentuation.characters import *
#exit

quizoutf = open('quizletvoc.tsv','w')
#do not run!
f = open('crosbycshaeffer2.0.xml')

#outf = open('cs2-2.xml','w')
prevpage = 0
prevpara = 0
curlesson = 0
sawvocab = 0
invocab = 0
gksent = 0
vocabitems = 0
totfreq = 0
csvocab = {}
csglosses = {}
for l in f:
    l = re.sub('@([0-9]+).*','<pb n="\g<1>"/>',l)
    l = re.sub('\n+$','',l)
    m = re.search('<pb n="([0-9]+)',l)
    if(m):
        curpage = int(m[1])
        if(not curpage == prevpage + 1):
            print('jumping from',prevpage,curpage)
        prevpage = curpage
    m = re.search('subtype="para"',l)
    if(m):
        invocab = 0
    if(re.search('^[0-9]+\.\s+.+[α-ω]',l)):
        gksent = gksent + 1
        #print(gksent,'gksent',l,end='')
    if(re.search('VOCAB',l)):
        sawvocab = 1
        invocab = 1
    m = re.search('<div type="textpart" subtype="lesson" n="([0-9]+)">',l)
    if(m):
        if( not sawvocab):
            print('missingvoc',curpage,curlesson)
       
        curlesson = m[1]
       
        sawvocab = 0
        l = re.sub('<div type="textpart" subtype="lesson">','<div type="textpart" subtype="lesson" n="'+str(curlesson)+'">',l)
    curlemma = ''
    m = re.search('^\s*<rs type="lemma" n="([^"]+)"',l)
    if(m):
        curlemma = m[1]
    elif(re.search('^\s*<rs type="lemma">([^<]+)',l)):
        m = re.search('^\s*<rs type="lemma">([^<]+)',l)
        curlemma = m[1]
    if(curlemma):
        vocabitems = vocabitems + 1
        if(not re.search('<rs',l)):
            l = re.sub('^([^ :,;]+)','<rs type="lemma">\g<1></rs>',l)
        curlemma = re.sub('-','',m[1])
        curlemma = strip_length(curlemma)
        csglosses[curlemma] = l
        if(not curlemma in csvocab):
            csvocab[curlemma] = []
        csvocab[curlemma].append(curlesson)
            #print(curlemma)
        if( not  curlemma in tbvoc):
            print('\nfailed',curlemma)
            curfreq = 0
        else:
            curfreq = tbvoc[curlemma]
            totfreq = totfreq + curfreq
        print(vocabitems, curlemma,curpage,curlesson,curfreq,totfreq,l,sep='\t')
        quizl = re.sub('<[^>]+>','',l)
        quizl = re.sub(':\s+','\t',quizl)
        print(vocabitems, curlemma,curpage,curlesson,curfreq,totfreq,quizl,sep='\t',file=quizoutf)
    #print(l,end='',file=outf)

quizoutf.close()

missingvoc 1 0
1	ἀδελφός	2	1	20	20	<rs type="lemma">ἀδελφός</rs>, ἀδελφοῦ, ὁ: brother.  PHILADELPHIA.

failed ἔχει
2	ἔχει	2	1	0	20	<rs type="lemma">ἔχει</rs>: he, she, or it has,

failed ἔχουσι
3	ἔχουσι	2	1	0	20	<rs type="lemma">ἔχουσι</rs>: they have.

failed ἦν
4	ἦν	2	1	0	20	<rs type="lemma">ἦν</rs>: he, she, it, or there was.

failed ἦσαν
5	ἦσαν	2	1	0	20	<rs type="lemma">ἦσαν</rs>: they or there were.

failed παύει
6	παύει	2	1	0	20	<rs type="lemma">παύει</rs>: he, she, or it stops (transitive).

failed παύουσι
7	παύουσι	2	1	0	20	<rs type="lemma">παύουσι</rs>: they stop.

failed πέμπει
8	πέμπει	2	1	0	20	<rs type="lemma">πέμπει</rs>: he, she, or it sends (transitive).

failed πέμπουσι
9	πέμπουσι	2	1	0	20	<rs type="lemma">πέμπουσι</rs>: they send.
10	ποταμός	2	1	99	119	<rs type="lemma">ποταμός</rs>, ποταμοῦ, ὁ: river, HIPPOPOTAMUS.
11	στρατηγός	2	1	151	270	<rs type="lemma">στρατηγός</rs>, στρατηγοῦ, ὁ: general. STRATEGY.
12	ἄνθρωπος	5	2	75	345	<rs type="lemma">ἄνθρωπος</rs>, ἀνθρώπου, 

Now let's see, for any given nouns, the verbs of which that noun is a direct object.

In [58]:
curdict = aobjnoms['ἀνήρ']
curword = 'ποταμός'
curword = 'ἄνθρωπος'
curword = 'πόλεμος'
curdict = aobjnoms[curword]
i = 0
print(len(curdict),greeklems[curword])
for foo in sorted(curdict,key=curdict.get,reverse=True):
    i = i + 1
    print(i,foo,curdict[foo])
    


1 21
1 ποιέω 1


In [59]:
def prepuse(curprep):
    curacc = 0
    curgen = 0
    curdat = 0
    if( curprep in prep_acc ):
        curacc = prep_acc[curprep]
    if( curprep in prep_gen ):
        curgen = prep_gen[curprep]
    if( curprep in prep_dat ):
        curdat = prep_dat[curprep]
    print(curprep,preplist[curprep],curgen,curdat,curacc,sep='\t')

print('curprep','total','gen.','dat.','acc.',sep='\t')
for foo in sorted(preplist,key=preplist.get,reverse=True):
    prepuse(foo)              

curprep	total	gen.	dat.	acc.
πρός	229	4	18	186
ἐν	210	4	202	0
διά	174	55	0	92
ἐπί	126	11	63	39
εἰς	102	0	0	96
περί	93	78	0	14
ὑπό	87	85	1	1
ἐκ	82	80	0	1
παρά	68	37	19	12
νή	65	0	0	64
ἀπό	50	48	0	1
μά	43	0	0	42
κατά	41	1	0	40
ἕνεκα	30	28	0	1
ἄνευ	23	22	0	0
ἀντί	21	16	0	0
μετά	19	16	0	3
ὑπέρ	15	13	0	2
σύν	14	0	12	0
μέχρι	14	13	0	1
ἕως	12	0	0	0
πρό	8	5	0	0
ἔμπροσθεν	3	1	0	0
πλησίον	2	2	0	0
ἀμφί	1	0	0	1
προπάροιθε	1	1	0	0
χωρίς	1	1	0	0
ἐναντίον	1	1	0	0
πέρα	1	1	0	0


In [60]:
len(depsdict)
i = 0
for foo in depsdict:
    i = i + 1
    print(i,foo,depsdict[foo])
    if(i>20):
        break

i = 0
for noun in formdict:
    matchart2 = ''

    headpos = get_postag(formdict[noun])
    curlemma = get_lemma(formdict[noun])
    if(not is_decl1(curlemma)):
        continue
    m = re.search('(.).(.---[mn].-)',headpos)
    if(m and m[1] == 'n'):
        matchpos = m[2]
        if(not noun in depsdict):
            continue
        matcharts = has_matchingarticle(noun,matchpos)
        if(not matcharts):
            continue
        if(len(matcharts) == 1):
            matchart = matcharts[0]
            matchart2 = ''
        elif(len(matcharts) == 2):
            matchart = matcharts[0]
            matchart2 = matcharts[1]
            print('2arts',matchart,matchart2)
        else:
            print('matcharts!=12',len(matcharts),matcharts)
            continue
        #print('art',matcharts,matchart)
        for boo in depsdict[noun]:
            if(not re.search('ATR',get_relation(formdict[boo]))):
                continue
            deppos = get_postag(formdict[boo])
            if(not is_decl1(get_lemma(formdict[boo]))):
                continue
            if( re.search('^a',deppos) and re.search(matchpos,deppos)):
                print()
                print(i,citdict[noun])
                #matchart2 = has_matchingarticle(boo,matchpos)

# a c b
# b a c
# b c a
# c a b
# c b a
# art adj noun
                if(matchart2):
                    print('bla2',matchart2)
                    if(matchart < noun and noun < matchart2 and matchart2 < boo):
                        print('attribx2:art noun art adj')
                        print(formdict[matchart])
                        print(formdict[noun])
                        print(formdict[matchart2])
                        print(formdict[boo])
                elif(matchart<boo and boo < noun):
                    i = i + 1
                    if(i>2000):
                        break
                    print('attrib1:article adjective noun')
                    if(re.search('lemma="αὐτός"',formdict[boo])):
                        print('thesame2')
                    print(formdict[matchart])
                    print(formdict[boo])
                    print(formdict[noun])
# adj art noun
                elif(boo<matchart and matchart < noun):
                    print('attrib2: adjective article noun')
                    if(re.search('lemma="αὐτός"',formdict[boo])):
                        print('intens2')
                    print(formdict[boo])
                    print(formdict[matchart])
                    print(formdict[noun])
 # art noun adj                   
                elif(matchart<noun and noun < boo):
                    print('attrib3:article noun adjective')
            
                    print('arts',matcharts)
                    print(formdict[matchart])
                    print(formdict[noun])
                    print(formdict[boo])
                    
                else:
                    print('attrib4')
                    print(formdict[noun])
                    print(formdict[matchart])
                    print(formdict[boo])
    


1 8919946 ['8919945', '8919951']
2 8919949 ['8919947']
3 8919951 ['8919948', '8919949', '8919950', '8919953', '8919955']
4 8919953 ['8919952', '8919954']
5 8919957 ['8919956']
6 8919955 ['8919957']
7 8919956 ['8919958', '8919960']
8 8919960 ['8919959']
9 8919945 ['8919961']
10 8919965 ['8919962']
11 8919970 ['8919963', '8919964', '8919965', '8919966', '8919968']
12 8919966 ['8919967']
13 8919968 ['8919969']
14 8919962 ['8919971']
15 8919972 ['8919973', '8919981', '8919982', '8919988']
16 8919978 ['8919974', '8919977']
17 8919981 ['8919975', '8919979', '8919980', '8919987']
18 8919977 ['8919976']
19 8919979 ['8919978']
20 8919986 ['8919983', '8919985']
21 8919987 ['8919984', '8919986']

0 1.1.18
attrib1:article adjective noun
    <word id="8921034" form="τὸν" lemma="ὁ" postag="l-s---ma-" head="8921036" relation="ATR"/>
    <word id="8921035" form="βουλευτικὸν" lemma="βουλευτικός" postag="a-s---ma-" head="8921036" relation="ATR"/>
    <word id="8921036" form="ὅρκον" lemma="ὅρκος" postag=

In [62]:
vparads = ['pia','iia','aia','fia','ria','lia','tia',
           'psa','asa','fsa','rsa','tsa',
           'poa','aoa','foa','roa','toa',
           'pma','ama','fma','rma','tma',
           'ppa','apa','fpa','rpa','tpa',
           'pna','ana','fna','rna','tna',
            
            'pim','iim','aim','fim','rim','lim','tim',
           'psm','asm','fsm','rsm','tsm',
           'pom','aom','fom','rom','tom',
           'pmm','amm','fmm','rmm','tmm',
           'ppm','apm','fpm','rpm','tpm',
           'pnm','anm','fnm','rnm','tnm',
            
            'pip','iip','aip','fip','rip','lip','tip',
           'psp','asp','fsp','rsp','tsp',
           'pop','aop','fop','rop','top',
           'pmp','amp','fmp','rmp','tmp',
           'ppp','app','fpp','rpp','tpp',
           'pnp','anp','fnp','rnp','tnp',
            
            'pie','iie','aie','fie','rie','lie','tie',
           'pse','ase','fse','rse','tse',
           'poe','aoe','foe','roe','toe',
           'pme','ame','fme','rme','tme',
           'ppe','ape','fpe','rpe','tpe',
           'pne','ane','fne','rne','tne',
           ]

tensenames = {
 "p" : "present",
 "i" : "imperfect",
 "r" : "perfect",
 "s" : "resultative",
 "a" : "aorist",
 "u" : "past",
 "l" : "pluperfect",
 "f" : "future",
 "t" : "future perfect",
 "x" : "uncertain tense"
}

moodnames = {
 "i" : "indicative",
 "s" : "subjunctive",
 "m" : "imperative",
 "o" : "optative",
 "n" : "infinitive",
 "p" : "participle",
 "d" : "gerund"
}

voicenames = {
    
 "a" : "active",
 "m" : "middle",
 "p" : "passive",
 "e" : "middle or passive",
 "x" : "unspecified",
}

totvbs  = 0
vparadcnt = {}
def countvparads(curparad):
    global totvbs
    f = open(curtb)
    vpat = 'postag=.v..(...)'
    
    for foo in vparads:
        vparadcnt[foo] = 0
    for l in f:
        m = re.search(vpat,l)
        if(m):
            curv = m[1]
            if(not curv in vparadcnt):
                print(l)
            else:
                vparadcnt[curv] = vparadcnt[curv] + 1
                totvbs = totvbs + 1
        
    
    f.close()

countvparads('pia')
i = 0
sofar = 0
print('total verbs',totvbs)
for foo in sorted(vparadcnt,key=vparadcnt.get,reverse=True):
    i = i + 1
    sofar = sofar + vparadcnt[foo]
    curshow = re.sub('(\.[0-9][0-9]).+','\g<1>',str(vparadcnt[foo]/totvbs))
    totshow = re.sub('(\.[0-9][0-9]).+','\g<1>',str(sofar/totvbs))
    #print(i,foo,vparadcnt[foo],vparadcnt[foo]/totvbs,sofar/totvbs)
    print(i,foo,vparadcnt[foo],curshow,totshow)

total verbs 8608
1 pna 1215 0.14 0.14
2 pia 1154 0.13 0.27
3 iia 1030 0.11 0.39
4 ppa 1018 0.11 0.51
5 pie 537 0.06 0.57
6 ppe 518 0.06 0.63
7 pne 455 0.05 0.68
8 poa 249 0.02 0.71
9 ana 228 0.02 0.74
10 apa 204 0.02 0.76
11 psa 154 0.01 0.78
12 aia 149 0.01 0.80
13 ria 143 0.01 0.81
14 rpa 108 0.01 0.83
15 poe 103 0.01 0.84
16 anm 100 0.01 0.85
17 asa 94 0.01 0.86
18 aoa 90 0.01 0.87
19 fim 87 0.01 0.88
20 iie 87 0.01 0.89
21 pse 83 0.00 0.90
22 apm 81 0.00 0.91
23 fia 78 0.00 0.92
24 rpe 74 0.00 0.93
25 aim 65 0.00 0.94
26 rna 50 0.00 0.94
27 app 45 0.00 0.95
28 rie 45 0.00 0.95
29 pma 39 0.00 0.96
30 aom 37 0.00 0.96
31 asm 36 0.00 0.97
32 ama 35 0.00 0.97
33 anp 27 0.00 0.97
34 fna 23 0.00 0.98
35 aip 23 0.00 0.98
36 fnm 21 0.00 0.98
37 rne 21 0.00 0.98
38 aop 17 0.00 0.99
39 pme 17 0.00 0.99
40 fpa 16 0.00 0.99
41 fpm 10 0.00 0.99
42 asp 10 0.00 0.99
43 roa 7 0.00 0.99
44 rma 5 0.00 0.99
45 lia 4 0.00 0.99
46 rsa 3 0.00 0.99
47 amm 3 0.00 0.99
48 foa 2 0.00 0.99
49 lim 2 0.00 0.99

In [63]:

stoplist = ['ὁ','καί','οὐκ', 'δέ','εἰμί','ἄπειμι']

def searchvoc(oldlemlist,searchlemlist,posfilts):
    oldlist = []
    #searchlem = searchlemlist[2]
    i = 0
    outf = open('currquest.tsv','w')
    #if(searchlem in greekforms and not searchlem in greeklems):
    #if(searchlem in greekforms and not intersection(searchlemlist,  greeklems)):
    if(1 and not intersection(searchlemlist,  greeklems)):
        print('sawform',searchlem)
        for foo in sorted(greeksentlens,key=greeksentlens.get):
            if(searchlem in greeksentforms[foo]):
                i = i + 1
                ind = greeksentforms[foo].index(searchlem)
                print('hit',i,engsentcits[foo],len(greeksentlems[foo]),foo,greeksentforms[foo][ind],greeksentpostags[foo][ind],greeksentrels[foo][ind])
                print(' '.join(greeksentforms[foo]))
                print(engsents[foo])
                print(' '.join(greeksentlems[foo]))
                print()
    else:
        for foo in sorted(greeksentlens,key=greeksentlens.get):
            #if(searchlem in greeksentlems[foo]):
            interl = intersection(searchlemlist+oldlemlist,  greeksentlems[foo])
            interl1 = intersection(oldlemlist,  greeksentlems[foo])
            if(interl and posfilts):
                workinterl = []
                if(len(posfilts)>1):
                    possearch = '('+'|'.join(posfilts) + ')'
                else:
                    possearch = posfilts[0]
                for cursearchlem in interl:
                    ind = greeksentlems[foo].index(cursearchlem)
                    if(re.search(possearch,greeksentpostags[foo][ind])):
                        workinterl.append(cursearchlem)
                interl = workinterl
            if(interl1 and 0):
                for goo in greeksentforms[foo]:
                    oldlist.append(goo)
                #newlist = greeksentforms[foo]
                i = i + 1
                for cursearchlem in interl1:
                    #if(cursearchlem in stoplist):
                     #   continue

                    ind = greeksentlems[foo].index(cursearchlem)
                    #newlist = greeksentforms[foo]
                    #print('old',oldlemlist,oldlemlist[ind])
            if(interl):
                newlist = []
                for goo in greeksentforms[foo]:
                    newlist.append(goo)
                #newlist = greeksentforms[foo]
                i = i + 1
                print(i,interl)
                answers = []
                sentrels = []
                for cursearchlem in interl:
                    if(cursearchlem in stoplist):
                        continue

                    ind = greeksentlems[foo].index(cursearchlem)
                    #newlist = greeksentforms[foo]
                    print('new',newlist,newlist[ind])
                    answers.append(newlist[ind]) 
                    sentrels.append(greeksentrels[foo][ind])
                    hiddenform = newlist[ind]
                    #newlist[ind] = '[______]'
                #just book 1 for now
                if(not re.search('^1',engsentcits[foo])):
                    continue
                print(i,foo,engsentcits[foo],end='\t',sep='\t',file=outf)
#print(i,engsentcits[foo],len(greeksentlems[foo]),foo,greeksentforms[foo][ind],greeksentpostags[foo][ind],greeksentrels[foo][ind])
                print(' '.join(newlist),' '.join(oldlist),engsents[foo],end='\t',sep='\t',file=outf)
                #print(engsents[foo],file=outf)
                #print(' '.join(greeksentlems[foo]))
                #print(' '.join(greeksentlems[foo]))
                print(interl,len(answers),answers,sentrels,file=outf,sep='\t')
                print()
    print('done' )      
    outf.close()       

def totvoclist(startn,lnum):
    vblist=[]
    nomlist = []
    oldlist = []
    for i in range(0,startn):
        curchap = str(i)
        
        for boo in csvocab:
            if(boo in stoplist):
                continue
            if( curchap in csvocab[boo]):
                #print(curchap,'got',boo,csvocab[boo])
                oldlist.append(boo)
        
    for i in range(startn,lnum+1):
        curchap = str(i)
        
        for boo in csvocab:
            if(boo in stoplist):
                continue
            if( curchap in csvocab[boo]):
                #print(curchap,'got',boo,csvocab[boo])
                if(re.search('(ω|όμαι)$',boo)):
                    vblist.append(boo)
                else:
                    nomlist.append(boo)
    return(oldlist,vblist,nomlist)

#vblist,nomlist = totvoclist(10)
#vblist12,nomlist12 = totvoclist(12)
#vblist13,nomlist13 = totvoclist(13)
#vblist14,nomlist14 = totvoclist(14)
#vblist15,nomlist15 = totvoclist(15)
#vblist16,nomlist16 = totvoclist(16)
#vblist17,nomlist17 = totvoclist(17)
#vblist22,nomlist22 = totvoclist(1,22)
oldlemmas,vblist24,nomlist24 = totvoclist(24,24)
#vblist25,nomlist25 = totvoclist(25,25)
#print(vblist)
#searchvoc(nomlist,[])
#searchvoc(['ὅς'],[])
#vblist12_16 = vblist12 + vblist13 + vblist14 + vblist15 + vblist16
#nomlist12_16 = nomlist12 + nomlist13 + nomlist14 + nomlist15 + nomlist16
#searchvoc(vblist12_16,['iia','pia','pna','fia','fna','aia','ana'])
#nomlist17_18 = nomlist17 + nomlist18
#searchvoc(nomlist18,[])
#searchvoc(['πᾶς'],[])
#searchvoc(vblist24,['iia','pia','pna','fia','fna','aia','ana',
                   # 'ppa','apa','fpa','iie','iip','pie','pim','pip'])
#oldlemmas,vblist25,nomlist25 = totvoclist(25,25)
#searchvoc(oldlemmas,vblist25+nomlist25,[])
oldlemmas,vblist4,nomlist4 = totvoclist(1,10)
#searchvoc(oldlemmas,vblist26+nomlist26,[])
#searchvoc(['ἀπό','ἐκ','ἐν','παρά','εἰς','διά','ἐπί','σύν','κατά','πρός'],[])
#searchvoc(vblist4,['iia','pia','pna','fia','fna'])
searchvoc([],vblist4,['pia'])
searchvoc([],nomlist4,[])


1 ['νομίζω']
new ['καὶ', 'τίνας', 'τούτους', 'νομίζεις', ';'] νομίζεις
2 ['ἐθέλω']
new ['οὐ', 'γὰρ', 'ἐθέλει', 'αὐτόματα', 'γίγνεσθαι', '.'] ἐθέλει
3 ['νομίζω']
new ['καὶ', 'τί', 'νομίζεις', 'δῆμον', 'εἶναι', ';'] νομίζεις
4 ['νομίζω']
new ['εὐμενεστέρους', 'δὲ', 'ποτέρους', 'ἑαυτοῖς', 'εἶναι', 'νομίζεις', ';'] νομίζεις
5 ['νομίζω']
new ['δουλείαν', 'δὲ', 'ποίαν', 'κακίστην', 'νομίζεις', 'εἶναι', ';'] νομίζεις
6 ['νομίζω']
new ['ἢ', 'νομίζεις', 'κακόνουν', 'τὴν', 'μητέρα', 'σοι', 'εἶναι', ';'] νομίζεις

7 ['ἔχω']
new ['ὦ', 'τλῆμον', ',', 'τί', 'δὲ', 'σὺ', 'ἀγαθὸν', 'ἔχεις', ';'] ἔχεις

8 ['ἔχω']
new ['φύσει', 'γὰρ', 'ἔχουσιν', 'οἱ', 'ἄνθρωποι', 'τὰ', 'μὲν', 'φιλικά', '·'] ἔχουσιν
9 ['ἔχω']
new ['πόθεν', 'οὖν', ',', 'ἔφη', ',', 'τὰ', 'ἐπιτήδεια', 'ἔχεις', ';'] ἔχεις
10 ['ἔχω']
new ['καὶ', 'ποῖα', ',', 'ἔφη', ',', 'ἐγὼ', 'δίκτυα', 'ἔχω', ';'] ἔχω
11 ['ἔχω']
new ['ἔχεις', 'οὖν', 'εἰπεῖν', 'ὁποῖός', 'τις', 'ὁ', 'εὐσεβής', 'ἐστιν', ';'] ἔχεις
12 ['νομίζω']
new ['καὶ', 'μέγα', 'νομίζομεν', '

1600 ['ἐντεῦθεν', 'ἀγορά', 'χώρα', 'εἰς']
new ['ἐντεῦθεν', 'ἐξελαύνει', 'σταθμοὺς', 'δύο', 'παρασάγγας', 'δώδεκα', 'ἐς', 'Κεράμων', 'ἀγοράν', ',', 'πόλιν', 'οἰκουμένην', ',', 'ἐσχάτην', 'πρὸς', 'τῇ', 'Μυσίᾳ', 'χώρᾳ', '.'] ἐντεῦθεν
new ['ἐντεῦθεν', 'ἐξελαύνει', 'σταθμοὺς', 'δύο', 'παρασάγγας', 'δώδεκα', 'ἐς', 'Κεράμων', 'ἀγοράν', ',', 'πόλιν', 'οἰκουμένην', ',', 'ἐσχάτην', 'πρὸς', 'τῇ', 'Μυσίᾳ', 'χώρᾳ', '.'] ἀγοράν
new ['ἐντεῦθεν', 'ἐξελαύνει', 'σταθμοὺς', 'δύο', 'παρασάγγας', 'δώδεκα', 'ἐς', 'Κεράμων', 'ἀγοράν', ',', 'πόλιν', 'οἰκουμένην', ',', 'ἐσχάτην', 'πρὸς', 'τῇ', 'Μυσίᾳ', 'χώρᾳ', '.'] χώρᾳ
new ['ἐντεῦθεν', 'ἐξελαύνει', 'σταθμοὺς', 'δύο', 'παρασάγγας', 'δώδεκα', 'ἐς', 'Κεράμων', 'ἀγοράν', ',', 'πόλιν', 'οἰκουμένην', ',', 'ἐσχάτην', 'πρὸς', 'τῇ', 'Μυσίᾳ', 'χώρᾳ', '.'] ἐς

1601 ['σκηνή']
new ['Κῦρος', 'δ’', 'οὖν', 'ἀνέβη', 'ἐπὶ', 'τὰ', 'ὄρη', 'οὐδενὸς', 'κωλύοντος', ',', 'καὶ', 'εἶδε', 'τὰς', 'σκηνὰς', 'οὗ', 'οἱ', 'Κίλικες', 'ἐφύλαττον', '.'] σκηνὰς

1602 ['δῆλος', 'μέν']
new ['ἄνδρ

new ['ἐλθόντων', 'μὲν', 'γὰρ', 'Περσῶν', 'καὶ', 'τῶν', 'σὺν', 'αὐτοῖς', 'παμπληθεῖ', 'στόλῳ', 'ὡς', 'ἀφανιούντων', 'τὰς', 'Ἀθήνας', ',', 'ὑποστῆναι', 'αὐτοὶ', 'Ἀθηναῖοι', 'τολμήσαντες', 'ἐνίκησαν', 'αὐτούς', '.'] μὲν
new ['ἐλθόντων', 'μὲν', 'γὰρ', 'Περσῶν', 'καὶ', 'τῶν', 'σὺν', 'αὐτοῖς', 'παμπληθεῖ', 'στόλῳ', 'ὡς', 'ἀφανιούντων', 'τὰς', 'Ἀθήνας', ',', 'ὑποστῆναι', 'αὐτοὶ', 'Ἀθηναῖοι', 'τολμήσαντες', 'ἐνίκησαν', 'αὐτούς', '.'] γὰρ
1872 ['ἐν', 'μέν']
new ['ὧν', 'ἔστι', 'μὲν', 'τεκμήρια', 'ὁρᾶν', 'τὰ', 'τρόπαια', ',', 'μέγιστον', 'δὲ', 'μαρτύριον', 'ἡ', 'ἐλευθερία', 'τῶν', 'πόλεων', 'ἐν', 'αἷς', 'ὑμεῖς', 'ἐγένεσθε', 'καὶ', 'ἐτράφητε', '·'] ἐν
new ['ὧν', 'ἔστι', 'μὲν', 'τεκμήρια', 'ὁρᾶν', 'τὰ', 'τρόπαια', ',', 'μέγιστον', 'δὲ', 'μαρτύριον', 'ἡ', 'ἐλευθερία', 'τῶν', 'πόλεων', 'ἐν', 'αἷς', 'ὑμεῖς', 'ἐγένεσθε', 'καὶ', 'ἐτράφητε', '·'] μὲν
1873 ['μέν', 'γάρ', 'εἰς']
new ['τότε', 'μὲν', 'γὰρ', 'ἄπειροι', 'ὄντες', 'αὐτῶν', 'τὸ', 'δὲ', 'πλῆθος', 'ἄμετρον', 'ὁρῶντες', ',', 'ὅμως', 'ἐτολμήσατε', 'σ

new ['καὶ', 'τέως', 'μὲν', 'αὐτοὺς', 'ἀναβαίνοντας', 'ὅπῃ', 'ἐδύναντο', 'ἕκαστος', 'οἱ', 'βάρβαροι', 'ἐτόξευον', 'καὶ', 'ἔβαλλον', ',', 'ἐγγὺς', 'δ’', 'οὐ', 'προσίεντο', ',', 'ἀλλὰ', 'φυγῇ', 'λείπουσι', 'τὸ', 'χωρίον', '.'] μὲν
new ['καὶ', 'τέως', 'μὲν', 'αὐτοὺς', 'ἀναβαίνοντας', 'ὅπῃ', 'ἐδύναντο', 'ἕκαστος', 'οἱ', 'βάρβαροι', 'ἐτόξευον', 'καὶ', 'ἔβαλλον', ',', 'ἐγγὺς', 'δ’', 'οὐ', 'προσίεντο', ',', 'ἀλλὰ', 'φυγῇ', 'λείπουσι', 'τὸ', 'χωρίον', '.'] ἀλλὰ
new ['καὶ', 'τέως', 'μὲν', 'αὐτοὺς', 'ἀναβαίνοντας', 'ὅπῃ', 'ἐδύναντο', 'ἕκαστος', 'οἱ', 'βάρβαροι', 'ἐτόξευον', 'καὶ', 'ἔβαλλον', ',', 'ἐγγὺς', 'δ’', 'οὐ', 'προσίεντο', ',', 'ἀλλὰ', 'φυγῇ', 'λείπουσι', 'τὸ', 'χωρίον', '.'] οὐ
2107 ['μέν', 'εἰς', 'ἐν', 'οὐ', 'γάρ']
new ['καὶ', 'γὰρ', 'ἦσαν', 'ὡπλισμένοι', 'ὡς', 'μὲν', 'ἐν', 'τοῖς', 'ὄρεσιν', 'ἱκανῶς', 'πρὸς', 'τὸ', 'ἐπιδραμεῖν', 'καὶ', 'φεύγειν', ',', 'πρὸς', 'δὲ', 'τὸ', 'εἰς', 'χεῖρας', 'δέχεσθαι', 'οὐχ', 'ἱκανῶς', '.'] μὲν
new ['καὶ', 'γὰρ', 'ἦσαν', 'ὡπλισμένοι', 'ὡς', 'μὲν', 'ἐν', 'το

new ['εἰ', 'δέ', 'τις', 'ὑμῶν', 'ἀθυμεῖ', 'ὅτι', 'ἡμῖν', 'μὲν', 'οὐκ', 'εἰσὶν', 'ἱππεῖς', ',', 'τοῖς', 'δὲ', 'πολεμίοις', 'πολλοὶ', 'πάρεισιν', ',', 'ἐνθυμήθητε', 'ὅτι', 'οἱ', 'μύριοι', 'ἱππεῖς', 'οὐδὲν', 'ἄλλο', 'ἢ', 'μύριοί', 'εἰσιν', 'ἄνθρωποι', '·'] μὲν
2328 ['βάρβαρος', 'ποταμός', 'μέν']
new ['εἰ', 'δὲ', 'ταῦτα', 'μὲν', 'γιγνώσκετε', 'ὅτι', 'κρείττονα', ',', 'τοὺς', 'δὲ', 'ποταμοὺς', 'ἄπορον', 'νομίζετε', 'εἶναι', 'καὶ', 'μεγάλως', 'ἡγεῖσθε', 'ἐξαπατηθῆναι', 'διαβάντες', ',', 'σκέψασθε', 'εἰ', 'ἄρα', 'τοῦτο', 'καὶ', 'μωρότατον', 'πεποιήκασιν', 'οἱ', 'βάρβαροι', '.'] βάρβαροι
new ['εἰ', 'δὲ', 'ταῦτα', 'μὲν', 'γιγνώσκετε', 'ὅτι', 'κρείττονα', ',', 'τοὺς', 'δὲ', 'ποταμοὺς', 'ἄπορον', 'νομίζετε', 'εἶναι', 'καὶ', 'μεγάλως', 'ἡγεῖσθε', 'ἐξαπατηθῆναι', 'διαβάντες', ',', 'σκέψασθε', 'εἰ', 'ἄρα', 'τοῦτο', 'καὶ', 'μωρότατον', 'πεποιήκασιν', 'οἱ', 'βάρβαροι', '.'] ποταμοὺς
new ['εἰ', 'δὲ', 'ταῦτα', 'μὲν', 'γιγνώσκετε', 'ὅτι', 'κρείττονα', ',', 'τοὺς', 'δὲ', 'ποταμοὺς', 'ἄπορον', 'νομίζετε', 

new ['ἐγώ', ',', 'ὦ', 'ἄνδρες', ',', 'θύομαι', 'μὲν', 'ὡς', 'ὁρᾶτε', 'ὁπόσα', 'δύναμαι', 'καὶ', 'ὑπὲρ', 'ὑμῶν', 'καὶ', 'ὑπὲρ', 'ἐμαυτοῦ', 'ὅπως', 'ταῦτα', 'τυγχάνω', 'καὶ', 'λέγων', 'καὶ', 'νοῶν', 'καὶ', 'πράττων', 'ὁποῖα', 'μέλλει', 'ὑμῖν', 'τε', 'κάλλιστα', 'καὶ', 'ἄριστα', 'ἔσεσθαι', 'καὶ', 'ἐμοί', '.'] ἄριστα
new ['ἐγώ', ',', 'ὦ', 'ἄνδρες', ',', 'θύομαι', 'μὲν', 'ὡς', 'ὁρᾶτε', 'ὁπόσα', 'δύναμαι', 'καὶ', 'ὑπὲρ', 'ὑμῶν', 'καὶ', 'ὑπὲρ', 'ἐμαυτοῦ', 'ὅπως', 'ταῦτα', 'τυγχάνω', 'καὶ', 'λέγων', 'καὶ', 'νοῶν', 'καὶ', 'πράττων', 'ὁποῖα', 'μέλλει', 'ὑμῖν', 'τε', 'κάλλιστα', 'καὶ', 'ἄριστα', 'ἔσεσθαι', 'καὶ', 'ἐμοί', '.'] κάλλιστα
new ['ἐγώ', ',', 'ὦ', 'ἄνδρες', ',', 'θύομαι', 'μὲν', 'ὡς', 'ὁρᾶτε', 'ὁπόσα', 'δύναμαι', 'καὶ', 'ὑπὲρ', 'ὑμῶν', 'καὶ', 'ὑπὲρ', 'ἐμαυτοῦ', 'ὅπως', 'ταῦτα', 'τυγχάνω', 'καὶ', 'λέγων', 'καὶ', 'νοῶν', 'καὶ', 'πράττων', 'ὁποῖα', 'μέλλει', 'ὑμῖν', 'τε', 'κάλλιστα', 'καὶ', 'ἄριστα', 'ἔσεσθαι', 'καὶ', 'ἐμοί', '.'] μὲν
2554 ['καλός', 'ἐν']
new ['ἐπὶ', 'δὲ', 'τούτῳ', 'ἐπιόντε

2739 ['ἐκ', 'μάχη', 'μέν', 'εἰς', 'ἐν', 'λόγος']
new ['ὅσα', 'μὲν', 'δὴ', 'ἐν', 'τῇ', 'ἀναβάσει', 'τῇ', 'μετὰ', 'Κύρου', 'ἔπραξαν', 'οἱ', 'Ἕλληνες', 'μέχρι', 'τῆς', 'μάχης', ',', 'καὶ', 'ὅσα', 'ἐπεὶ', 'Κῦρος', 'ἐτελεύτησεν', 'ἐν', 'τῇ', 'πορείᾳ', 'μέχρι', 'εἰς', 'τὸν', 'Πόντον', 'ἀφίκοντο', ',', 'καὶ', 'ὅσα', 'ἐκ', 'τοῦ', 'Πόντου', 'πεζῇ', 'ἐξιόντες', 'καὶ', 'ἐκπλέοντες', 'ἐποίουν', 'μέχρι', 'ἔξω', 'τοῦ', 'στόματος', 'ἐγένοντο', 'ἐν', 'Χρυσοπόλει', 'τῆς', 'Ἀσίας', ',', 'ἐν', 'τῷ', 'πρόσθεν', 'λόγῳ', 'δεδήλωται', '.'] ἐκ
new ['ὅσα', 'μὲν', 'δὴ', 'ἐν', 'τῇ', 'ἀναβάσει', 'τῇ', 'μετὰ', 'Κύρου', 'ἔπραξαν', 'οἱ', 'Ἕλληνες', 'μέχρι', 'τῆς', 'μάχης', ',', 'καὶ', 'ὅσα', 'ἐπεὶ', 'Κῦρος', 'ἐτελεύτησεν', 'ἐν', 'τῇ', 'πορείᾳ', 'μέχρι', 'εἰς', 'τὸν', 'Πόντον', 'ἀφίκοντο', ',', 'καὶ', 'ὅσα', 'ἐκ', 'τοῦ', 'Πόντου', 'πεζῇ', 'ἐξιόντες', 'καὶ', 'ἐκπλέοντες', 'ἐποίουν', 'μέχρι', 'ἔξω', 'τοῦ', 'στόματος', 'ἐγένοντο', 'ἐν', 'Χρυσοπόλει', 'τῆς', 'Ἀσίας', ',', 'ἐν', 'τῷ', 'πρόσθεν', 'λόγῳ', 'δεδήλωται', '.'] 

In [21]:
nomlist4

['ἀδελφός',
 'ἔχει',
 'ἔχουσι',
 'ἦν',
 'ἦσαν',
 'παύει',
 'παύουσι',
 'πέμπει',
 'πέμπουσι',
 'ποταμός',
 'στρατηγός',
 'ἄνθρωπος',
 'ἄξιος',
 'ἀπό',
 'δίκαιος',
 'Ἑλλήσποντος',
 'ἐκ',
 'μακρός',
 'μικρός',
 'πόλεμος',
 'πολέμιος',
 'φίλος',
 'ἀγαθός',
 'ἄγγελος',
 'ἵππος',
 'καλός',
 'κίνδυνος',
 'λίθος',
 'ἐν',
 'δένδρον',
 'παρά',
 'δῆλος',
 'δῶρον',
 'εἰς',
 'πεδίον',
 'στάδιον',
 'γάρ',
 'σπονδή',
 'κώμη',
 'μάχη',
 'οὐ',
 'φυγή',
 'φυλακή',
 'σκηνή',
 'ἀγορά',
 'ἀρχή',
 'δέκα',
 'διά',
 'ἐπιτήδειος',
 'ἡμέρα',
 'στρατιά',
 'φιλία',
 'φίλιος',
 'χώρα',
 'ἀλλά',
 'ἀρχαῖος',
 'βάρβαρος',
 'ἔργον',
 'κραυγή',
 'λόγος',
 'μέν',
 'σιγή',
 'θύρα',
 'ὁδός',
 'ἰσχυρός',
 'ἐνταῦθα',
 'λοιπός',
 'ἐντεῦθεν',
 'ἐπιστολή',
 'οἰκία',
 'πύλη']

In [64]:

from tabulate import tabulate
from prettytable import PrettyTable


            
outf = open('parads/test.md','w')

nparad1 = ['s---Zv','s---Zn','s---Zg','s---Zd','s---Za',
           'p---Zv','p---Zn','p---Zg','p---Zd','p---Za']
nparads = ['s---mv','s---mn','s---mg','s---md','s---ma',
            'p---mv','p---mn','p---mg','p---md','p---ma',
            's---fv','s---fn','s---fg','s---fd','s---fa',
            'p---fv','p---fn','p---fg','p---fd','p---fa',
            's---nv','s---nn','s---ng','s---nd','s---na',
            'p---nv','p---nn','p---ng','p---nd','p---na']

def printnounrow(useparad,curparad,curparadf,index,outf):
    if(re.search(',',curparad[useparad[index]])):
        rowvalue1 = curparad[useparad[index]]
    else:
        rowvalue1 = re.sub('\s+[0-9]+$','',curparad[useparad[index]])
    if(re.search(',',curparad[useparad[index+5]])):
        rowvalue2 = curparad[useparad[index+5]]
    else:
        rowvalue2 = re.sub('\s+[0-9]+$','',curparad[useparad[index+5]])
    print('| ' + defart_forms[useparad[index]],
          rowvalue1,
          #curparad[useparad[index]],
          curparadf[useparad[index]],
          defart_forms[useparad[index+5]],
          rowvalue2,
          #curparad[useparad[index+5]],
          str(curparadf[useparad[index+5]])+' |',file=outf,sep="|")

def printadjrow(useparad,curparad,curparadf,index,outf):
    curcasenum = useparad[index][5].upper()
    if(re.search(',',curparad[useparad[index]])):
        rowvalue1 = curparad[useparad[index]]
    else:
        rowvalue1 = re.sub('\s+[0-9]+$','',curparad[useparad[index]])
    if(re.search(',',curparad[useparad[index+10]])):
        rowvalue2 = curparad[useparad[index+10]]
    else:
        rowvalue2 = re.sub('\s+[0-9]+$','',curparad[useparad[index+10]])
    if(re.search(',',curparad[useparad[index+20]])):
        rowvalue3 = curparad[useparad[index+20]]
    else:
        rowvalue3 = re.sub('\s+[0-9]+$','',curparad[useparad[index+20]])
    print('| ' + curcasenum, 
          #curparad[useparad[index]],
          rowvalue1,
          curparadf[useparad[index]],
          #curparad[useparad[index+10]],
          rowvalue2,
          curparadf[useparad[index+10]],
          #curparad[useparad[index+20]],
          rowvalue3,
          str(curparadf[useparad[index+20]])+' |',file=outf,sep="|")

genders = ['m','f','n']
def printadjparad(curmasc,outf):
    if(not curmasc in lemma_pos_forms):
        print(curmasc,0)
        return

    
    curforms = lemma_pos_forms[curmasc]
    curparad = {}
    curparadf = {}
    for foo in nparads:
        for boo in curforms:
            m = re.search('('+foo+')',boo)
            if(m):
                #print(boo,lemma_pos_forms[curmasc],lemma_pos_forms[curmasc][boo])
                if(foo in curparadf):
                    curparadf[foo] = curforms[boo] + curparadf[foo]
                    if(curparad[foo] == 'NA'):
                        curparad[foo] = re.sub('[^:]+:','',boo)   + ' ' + str(curforms[boo])
                    else:   
                        curparad[foo] = curparad[foo] + ', ' + re.sub('[^:]+:','',boo)  + ' ' + str(curforms[boo])
                        print('hasnum',foo,curparad[foo],curparadf[foo])
                else:
                    curparadf[foo] = curforms[boo]
                    curparad[foo] = re.sub('[^:]+:','',boo) + ' ' + str(curforms[boo])
                print(foo,boo,curparadf[foo])
        for foo in nparads:
            if(not foo in curparad):
                curparad[foo] = 'NA'
                curparadf[foo] = 0
                #print('usetag',usetag)
                
    for foo in curparad:
        print('adj',foo,curparad[foo],curparadf[foo])
    
        
    print('\n',file=outf)
    print('##',curmasc,greeklems[curmasc],file=outf)
    
    print('|case | masc | # | fem  | #| neut  | #|',file=outf)
    print('| --- | --- | --- | --- | --- | --- | ---  |',file=outf)
    print('| Sing | |  |  | |  |   |',file=outf)
    
    for i in range(0,10):
        if(i == 5):
            print('| Plural | |  |  | |  |   |',file=outf)
        print(nparads[i],nparads[i+9],nparads[i+18])
        
        printadjrow(nparads,curparad,curparadf,i,outf)



def printnomparad(curgend,curmasc,outf):
    useparad = []
    for foo in nparad1:
        useparad.append(re.sub('Z',curgend,foo))
    
    if(not curmasc in lemma_pos_forms):
        print(curmasc,0)
        return

    curparad = {}
    curparadf = {}
    for foo in useparad:
        for boo in lemma_pos_forms[curmasc]:
            if(re.search(foo,boo)):
                #print(boo,lemma_pos_forms[curmasc],lemma_pos_forms[curmasc][boo])
                curparad[foo] = re.sub('[^:]+:','',boo) + ' ' + str(lemma_pos_forms[curmasc][boo])
                print('foo',foo,curparad[foo])
                curparadf[foo] = lemma_pos_forms[curmasc][boo]
                #print(foo,boo,curparadf[foo])
        for foo in useparad:
            if(not foo in curparad):
                curparad[foo] = 'NA'
                curparadf[foo] = 0
                
        
    
    
    print('| sg | | # | pl | | #|',file=outf)
    print('| --- | --- | --- | --- | --- | --- |',file=outf)
    
    
    printnounrow(useparad,curparad,curparadf,0,outf)
    printnounrow(useparad,curparad,curparadf,1,outf)
    printnounrow(useparad,curparad,curparadf,2,outf)
    printnounrow(useparad,curparad,curparadf,3,outf)
    printnounrow(useparad,curparad,curparadf,4,outf)

    print('\n\n',file=outf)

def nomgenders(curnom,outf):
    gendtable = {}
    print('\n',file=outf)
    print('##',curnom,greeklems[curnom],file=outf)

    for boo in lemma_pos_forms[curnom]:
        if(boo[0] in ['n','p']):
            curgend = boo[6]
            if(curgend in gendtable):
                gendtable[curgend] = gendtable[curgend] + lemma_pos_forms[curnom][boo]
            else:
                gendtable[curgend] = lemma_pos_forms[curnom][boo]
                
    for foo in gendtable:
        printnomparad(foo,curnom,outf)

            

    
curmasc = 'πολέμιος'
printadjparad(curmasc,outf)
    
curmasc = 'πᾶς'
printadjparad(curmasc,outf)
    
curmasc = 'φίλος'
printadjparad(curmasc,outf)

curmasc = 'στάδιον'
nomgenders(curmasc,outf)
curmasc = 'δῶρον'
nomgenders(curmasc,outf)
curmasc = 'γυνή'
nomgenders(curmasc,outf)
curmasc = 'ἀδελφός'
nomgenders(curmasc,outf)
curmasc = 'ποταμός'
nomgenders(curmasc,outf)

curmasc = 'κώμη'
nomgenders(curmasc,outf)

curmasc = 'μάχη'
nomgenders(curmasc,outf)

curmasc = 'σκηνή'
nomgenders(curmasc,outf)

curmasc = 'σπονδή'
nomgenders(curmasc,outf)

curmasc = 'φυγή'
nomgenders(curmasc,outf)

curmasc = 'φυλακή'
nomgenders(curmasc,outf)

curmasc = 'ἀνήρ'
nomgenders(curmasc,outf)

curmasc = 'παῖς'
nomgenders(curmasc,outf)

printadjparad('ἐπιτήδειος',outf)
nomgenders('στάδιον',outf)
outf.close()


s---mg a-s---mg-:πολεμίου 1
p---mn a-p---mn-:πολέμιοι 2
p---mg a-p---mg-:πολεμίων 5
p---md a-p---md-:πολεμίοις 1
p---ma a-p---ma-:πολεμίους 13
adj s---mv NA 0
adj s---mn NA 0
adj s---mg πολεμίου 1 1
adj s---md NA 0
adj s---ma NA 0
adj p---mv NA 0
adj p---mn πολέμιοι 2 2
adj p---mg πολεμίων 5 5
adj p---md πολεμίοις 1 1
adj p---ma πολεμίους 13 13
adj s---fv NA 0
adj s---fn NA 0
adj s---fg NA 0
adj s---fd NA 0
adj s---fa NA 0
adj p---fv NA 0
adj p---fn NA 0
adj p---fg NA 0
adj p---fd NA 0
adj p---fa NA 0
adj s---nv NA 0
adj s---nn NA 0
adj s---ng NA 0
adj s---nd NA 0
adj s---na NA 0
adj p---nv NA 0
adj p---nn NA 0
adj p---ng NA 0
adj p---nd NA 0
adj p---na NA 0
s---mv p---ma p---fd
s---mn s---fv p---fa
s---mg s---fn s---nv
s---md s---fg s---nn
s---ma s---fd s---ng
p---mv s---fa s---nd
p---mn p---fv s---na
p---mg p---fn p---nv
p---md p---fg p---nn
p---ma p---fd p---ng
s---mg a-s---mg-:παντός 6
s---md a-s---md-:παντί 2
s---ma a-s---ma-:πάντα 8
p---mn a-p---mn-:πάντες 13
p---mg a-p---mg-:πάν

KeyError: 'ποταμός'

In [23]:

anttb = '/Users/gcrane/github/Daphne/data/annotation/latest/tlg0011/tlg002/tlg0011.tlg002.daphne_tb-grc1.conllu'
antvoc = {}
antvoc_sh = {}
f = open(anttb)

curln = 0
wordtype = {}
for l in f:
    m = re.search('Ref=([0-9]+)',l)
    if(m):
        curln = int(m[1])
    if(not re.search('^[0-9]+\s',l)):
        continue
    if(re.search('PUNCT',l)):
        continue
    args = l.split()

    lemma = args[2]
    if(lemma in antvoc):
        antvoc[lemma] = 1 + antvoc[lemma]
    else:
        antvoc[lemma] = 1
    if( curln < 100):
        antvoc_sh[lemma] = 1
    wordtype[lemma] = args[4][0]
    #print(curln,lemma)

i  = 0
new = 0
outf = open('antigonevoc.tsv','w')
print('Freq. in Ant.','CS lesson','gloss','type',file=outf)
for foo in sorted(antvoc,key=antvoc.get,reverse=True):
    i = i + 1
    if(not foo in antvoc_sh):
        continue
    if(foo in csvocab and int(csvocab[foo][0]) < 21):
        curless = csvocab[foo][0]
    else:
        curless = 'new'
        new = new + 1
    if(foo in lexicalentries):
        curgloss = lexicalentries[foo]
    else:
        curgloss = 'nodef'
    if(foo in wordtype):
        curtype = wordtype[foo]
    else:
        curtype = 'NA'
    
    print(antvoc[foo],curless,foo,curgloss,curtype,sep='\t',file=outf)
    print(antvoc[foo],curless,foo,curgloss,curtype,sep='\t')
    
    #else:
    #    print(foo,antvoc[foo],'hit')
f.close()
outf.close()

377	new	ὁ	the	l
253	3	καί	and	c
192	4	δέ	but	d
162	15	ἐγώ	I (first person pronoun)	p
127	14	ὅδε	this	p
114	6	γάρ	for	d
112	6	οὐ	not	d
101	15	σύ	you (personal pronoun)	p
88	17	εἰμί	to be	v
85	14	οὗτος	this; that	p
82	new	οὔτε	neither / nor	c
70	8	ἀλλά	otherwise	c
69	new	τε	and	c
64	4	ἐν	in	r
55	15	μή	not	d
54	new	ὡς	as	c
54	new	ἄν1	nodef	d
53	new	τις	any one	p
53	15	κακός	bad	a
53	10	ἔχω	to have	v
52	13	ὅς	who	p
51	new	τίς	who? which?	p
50	2	ἐκ	from out of	r
49	8	μέν	on the one hand	d
47	15	εἰ	conj. if	c
45	new	λέγω	to pick; to say	v
42	new	ἀνήρ	a man	n
39	new	θνήσκω	nodef	v
39	new	γε	at least	d
39	new	θεός	god	n
37	new	ὦ	O! oh!	i
37	new	οὐδείς	not one	p
37	new	ἤ	either..or; than	c
37	new	πᾶς	all	p
34	new	πόλις	a city	n
34	18	πρός	(w. gen.) from; (w. dat.) at	r
31	12	ἐπί	on	r
30	13	αὐτός	unemph. 3rd pers.pronoun; -self; [the] same 	p
29	new	οἶδα	to know	v
25	2	φίλος	friend; loved	a
25	new	ποτέ	nodef	d
24	new	ὁράω	to see	v
24	new	ὅστις	indef. relative or indirect interrogative	p
23	new	ἐ

In [24]:
i = 0
for foo in csvocab:
    if(not foo in tbvoc):
        i = i + 1
        print(i,foo,csvocab[foo])

1 ἔχει ['1']
2 ἔχουσι ['1']
3 ἦν ['1']
4 ἦσαν ['1']
5 παύει ['1']
6 παύουσι ['1']
7 πέμπει ['1']
8 πέμπουσι ['1']
9 φασί(ν) ['17']
10 φησί(ν) ['17']
11 πότε ['29']
12 ῥήτωρ ['38']
13 θεμιστοκλῆς ['39']
14 χείρων ['42']
15 χείριστος ['42']
16 μνῆμα ['48']
17 ἀλλάσσω ['49']
18 εἴθε ['51']
19 πέποιθα ['52']
20 θνήσκω ['52']
21 φύσις ['54']
22 ἦρα ['64']
23 δίς ['65']
24 διαγιγνώσκω ['72']


In [25]:
wordtype

{'ὦ': 'i',
 'κοινός': 'a',
 'αὐτάδελφος': 'a',
 'Ἰσμήνη': 'n',
 'κάρα': 'n',
 'ἆρα': 'd',
 'οἶδα': 'v',
 'ὅς': 'p',
 'τις': 'p',
 'Ζεύς': 'n',
 'ὁ': 'l',
 'ἀπό': 'r',
 'Οἰδίπους': 'n',
 'κακός': 'a',
 'ὁποῖος': 'p',
 'οὐ': 'd',
 'ἐγώ': 'p',
 'ἔτι': 'd',
 'ζάω': 'v',
 'τελέω': 'v',
 'οὐδείς': 'p',
 'γάρ': 'd',
 'οὔτε': 'c',
 'ἀλγεινός': 'a',
 'ἄτη': 'n',
 'ἄτερ': 'r',
 'αἰσχρός': 'a',
 'ἄτιμος': 'd',
 'εἰμί': 'v',
 'σός': 'p',
 'τε': 'c',
 'καί': 'c',
 'ἐμός': 'p',
 'ὁράω': 'v',
 'νῦν': 'd',
 'τίς': 'p',
 'οὗτος': 'p',
 'αὖ': 'd',
 'φημί': 'v',
 'πάνδημος': 'a',
 'πόλις': 'n',
 'κήρυγμα': 'n',
 'τίθημι': 'v',
 'στρατηγός': 'n',
 'ἄρτιος': 'd',
 'ἔχω': 'v',
 'εἰσακούω': 'v',
 'ἤ': 'c',
 'σύ': 'p',
 'λανθάνω': 'v',
 'πρός': 'r',
 'φίλος': 'a',
 'στείχω': 'v',
 'ἐχθρός': 'a',
 'μέν': 'd',
 'μῦθος': 'n',
 'Ἀντιγόνη': 'n',
 'ἡδύς': 'a',
 'ἱκνέομαι': 'v',
 'ἐκ': 'r',
 'ὅστις': 'p',
 'δύο': 'm',
 'ἀδελφός': 'n',
 'στερέω': 'v',
 'εἷς': 'n',
 'θνήσκω': 'v',
 'ἡμέρα': 'n',
 'διπλός': 'a',
 'χείρ

In [26]:
i = 0
j = 0
seentokens = 0
for foo in sorted(tbvoc,key=tbvoc.get,reverse=True):
    if(foo[0].isupper()):
        continue
    i= i + 1
    if(i>5000):
        break
    if(not foo in csvocab):
        cv = 'NA'
    else:
        cv = csvocab[foo]
        
    if(   cv == 'NA'):
        j = j + 1
        seentokens = seentokens + tbvoc[foo]
        if(j<500):
            print(i,j,seentokens,tbvoc[foo],foo,cv)
print(tottokens,seentokens,seentokens/tottokens,.8*tottokens)

1 1 6522 6522 ὁ NA
65 2 6644 122 ἀπέρχομαι NA
69 3 6755 111 δεῖ NA
76 4 6860 105 ὥστε NA
107 5 6938 78 οἴομαι NA
136 6 6995 57 ἀνίστημι NA
141 7 7050 55 σταθμός NA
149 8 7101 51 τρεῖς NA
152 9 7151 50 ἀμφί NA
161 10 7197 46 δύο NA
179 11 7237 40 εἴκοσι NA
187 12 7275 38 προσέρχομαι NA
189 13 7313 38 καταλαμβάνω NA
192 14 7350 37 οἴχομαι NA
195 15 7386 36 καταλείπω NA
198 16 7422 36 τοσοῦτος NA
205 17 7457 35 ἐξέρχομαι NA
206 18 7492 35 ἀπαγγέλλω NA
208 19 7526 34 παραγγέλλω NA
213 20 7560 34 παρέρχομαι NA
218 21 7593 33 ἅπας NA
223 22 7624 31 ἄκρον NA
227 23 7655 31 παραδίδωμι NA
231 24 7685 30 καταβαίνω NA
232 25 7715 30 ὑποζύγιον NA
240 26 7744 29 ἀναβαίνω NA
241 27 7773 29 συλλέγω NA
250 28 7801 28 τριάκοντα NA
259 29 7828 27 ἐπιτίθημι NA
261 30 7855 27 μηδείς NA
263 31 7882 27 συνέρχομαι NA
264 32 7908 26 πρέσβυς NA
265 33 7934 26 καθίστημι NA
268 34 7960 26 ὅσπερ NA
275 35 7985 25 τέσσαρες NA
283 36 8009 24 ἐπέρχομαι NA
312 37 8031 22 διαπράσσω NA
313 38 8053 22 χιών NA
318 39 807

In [27]:
csvocab

{'ἀδελφός': ['1'],
 'ἔχει': ['1'],
 'ἔχουσι': ['1'],
 'ἦν': ['1'],
 'ἦσαν': ['1'],
 'παύει': ['1'],
 'παύουσι': ['1'],
 'πέμπει': ['1'],
 'πέμπουσι': ['1'],
 'ποταμός': ['1'],
 'στρατηγός': ['1'],
 'ἄνθρωπος': ['2'],
 'ἄξιος': ['2'],
 'ἀπό': ['2'],
 'δίκαιος': ['2'],
 'Ἑλλήσποντος': ['2'],
 'ἐκ': ['2'],
 'μακρός': ['2'],
 'μικρός': ['2', '42', '42'],
 'πόλεμος': ['2'],
 'πολέμιος': ['2'],
 'φίλος': ['2'],
 'ἀγαθός': ['3', '42', '42', '42', '42'],
 'ἄγγελος': ['3'],
 'ἄγω': ['3'],
 'γράφω': ['3'],
 'ἐθέλω': ['3'],
 'ἵππος': ['3'],
 'καί': ['3'],
 'καλός': ['3', '28', '42', '42'],
 'κίνδυνος': ['3'],
 'λίθος': ['3'],
 'λύω': ['3'],
 'παύω': ['3'],
 'δέ': ['4'],
 'ἐν': ['4'],
 'δένδρον': ['4'],
 'παρά': ['4'],
 'δῆλος': ['4'],
 'δῶρον': ['4'],
 'εἰς': ['4'],
 'πεδίον': ['4'],
 'στάδιον': ['4'],
 'γάρ': ['6'],
 'σπονδή': ['6'],
 'κώμη': ['6'],
 'μάχη': ['6'],
 'φεύγω': ['6'],
 'οὐ': ['6'],
 'φυγή': ['6'],
 'φυλακή': ['6'],
 'σκηνή': ['6'],
 'φυλάσσω': ['6'],
 'ἀγορά': ['7'],
 'ἀρχή': ['7']

In [28]:
paradpats = {}
paradpats['ostem_m1'] = 'form="([^"]+)" lemma="([^"]+ός)" postag="(n.....m[^"]+)'
paradpats['h_hs_h'] = 'form="([^"]+)" lemma="([^"]+[^ίέριε][ηή])" postag="(n.....f[^"]+)'
paradpats['h_hs_La'] = 'form="([^"]+)" lemma="([^"]+[ίέρ][ηα])" postag="(n.....f[^"]+)'
paradpats['defart_m'] = 'form="([^"]+)" lemma="(ὁ)" postag="(l.....m[^"]+)'
paradpats['defart_n'] = 'form="([^"]+)" lemma="(ὁ)" postag="(l.....n[^"]+)'
paradpats['defart_f'] = 'form="([^"]+)" lemma="(ὁ)" postag="(l.....f[^"]+)'
paradpats['wstem_3.pia'] = 'form="([^"]+)" lemma="([^"]+[^άέό]ω)" postag="(v3.pia[^"]+)'
paradpats['wstem_pia'] = 'form="([^"]+)" lemma="([^"]+[^άέό]ω)" postag="(v..pia[^"]+)'
paradpats['wstem_iia'] = 'form="([^"]+)" lemma="([^"]+[^άέό]ω)" postag="(v..iia[^"]+)'
paradpats['wstem_pna'] = 'form="([^"]+)" lemma="([^"]+[^άέό]ω)" postag="(v..pia[^"]+)'
paradpats['regfut_fia'] = 'form="([^"]+)" lemma="([^"ῖῦῶ]+ω)" postag="(v..fia[^"]+)'
paradpats['regfut_fna'] = 'form="([^"]+)" lemma="([^"ῖῦῶ]+ω)" postag="(v..fna[^"]+)'
#lesson 10 covers 1st and 2nd aorists both
paradpats['aor_aia'] = 'form="([^"]+[^ηω])" lemma="([^"]+ω)" postag="(v..aia[^"]+)'
paradpats['aor_ana'] = 'form="([^"]+[^ηω])" lemma="([^"]+ω)" postag="(v..ana[^"]+)'

paradpats['ostem_m2'] = 'form="([^"]+)" lemma="([^"]+ος)" postag="(n.....m[^"]+)'
paradpats['ostem_n'] = 'form="([^"]+)" lemma="([^"]+[οό]ν)" postag="(n.....n[^"]+)'

paradpats['adj1_m'] = 'form="([^"]+)" lemma="([^"]+[οό]ς)" postag="(a.....m[^"]+)'
paradpats['adj1_n'] = 'form="([^"]+)" lemma="([^"]+[οό]ς)" postag="(a.....n[^"]+)'
paradpats['adj1_f'] = 'form="([^"]+)" lemma="([^"]+[οό]ς)" postag="(a.....f[^"]+)'

paradpats['hos_m'] = 'form="([^"]+)" lemma="(ὅς)" postag="(p.....m[^"]+)'
paradpats['hos_n'] = 'form="([^"]+)" lemma="(ὅς)" postag="(p.....n[^"]+)'
paradpats['seautou_m'] = 'form="([^"]+)" lemma="(σεαυτοῦ)" postag="(p.....m[^"]+)'
paradpats['emautou_m'] = 'form="([^"]+)" lemma="(ἐμαυτοῦ)" postag="(p.....m[^"]+)'
paradpats['autos_m'] = 'form="([^"]+)" lemma="(αὐτός)" postag="(a.....m[^"]+)'
paradpats['hode_m'] = 'form="([^"]+)" lemma="(ὅδε)" postag="(a.....m[^"]+)'

#recessive
paradpats['w_p_mp'] = 'form="([^"]+)" lemma="([^"]+ω)" postag="(v..[fp]p[mep][^"]+)'
paradpats['w_a_m'] = 'form="([^"]+)" lemma="([^"]+ω)" postag="(v..ap[me][^"]+)'

lemma_class = {}

lesson01 = ['ostem_m1','defart_m','wstem_3.pia','hos_m','autos_m','hode_m','seautou_m','emautou_m','w_p_mp','w_a_m']
lesson02 = ['ostem_m2','adj1_m','w_p_mp','w_a_m']
lesson03 = ['wstem_pia','wstem_pna']
lesson04 = ['ostem_n','adj1_n','defart_n','hos_n']
lesson06 = ['h_hs_h','adj1_f','defart_f']
lesson07 = ['h_hs_La']
lesson08 = ['wstem_iia']
lesson09 = ['regfut_fia','regfut_fna']
lesson10 = ['aor_aia','aor_ana']

curlesson = lesson06
curlesson = lesson10

def add_lemma(pclass,lemma):
    if(not pclass in lemma_class):
        lemma_class[pclass] = {}
    curdict = lemma_class[pclass]
    if(lemma in curdict):
        curdict[lemma] = curdict[lemma] + 1
    else:
        curdict[lemma] = 1
    #lemma_class[pclass] = curdict

def addparad(curpclass,l):
    m = re.search(paradpats[curpclass],l)
    if(m):
        curform = m[1]
        curlemma = m[2]
        curpostag = m[3]
        add_lemma(curpclass,curlemma)
    
def getparadpats(fname):
    global paradpats
    
    f = open(fname)
    for l in f:
        l = re.sub('\n','',l)
        
        for foo in curlesson:
            #print('doing',foo)
            addparad(foo,l)
    
    
    f.close()
 
getparadpats(curtb)

k = 0
for foo in curlesson:
    curdict = lemma_class[foo]

    print(foo,len(curdict))

    i = 0
    j = 0
    for foo in sorted(curdict,key=curdict.get,reverse=True):
        i = i + 1
        j = j + curdict[foo]
        k = k + curdict[foo]
        if(not foo in lexicalentries):
            shortdef = 'nodef'
        else:
            shortdef = lexicalentries[foo]
        print(i,j,k,foo,curdict[foo],shortdef)


aor_aia 250
1 175 175 λέγω 175 to pick; to say
2 227 227 δοκέω 52 seem
3 259 259 ὁράω 32 to see
4 288 288 μένω 29 to stay at home
5 316 316 λαμβάνω 28 to take
6 343 343 κελεύω 27 to urge
7 367 367 ποιέω 24 to make
8 389 389 ἀποθνῄσκω 22 to die
9 403 403 ἀκούω 14 to hear
10 416 416 πέμπω 13 to send
11 428 428 τυγχάνω 12 (with gen.) to hit the mark
12 438 438 παραγγέλλω 10 to transmit as a message; give orders
13 447 447 ἀποκτείνω 9 to kill
14 456 456 φεύγω 9 to flee
15 465 465 πάσχω 9 to experience
16 472 472 γιγνώσκω 7 to learn to know
17 479 479 ἐπιχειρέω 7 to attempt
18 486 486 ἀνακράζω 7 to cry out
19 492 492 τελευτάω 6 to complete
20 498 498 διαβαίνω 6 to cross (a river
21 504 504 ἀπαγγέλλω 6 to bring tidings
22 510 510 κηρύσσω 6 to be a herald
23 515 515 θαυμάζω 5 to wonder
24 520 520 ἀδικέω 5 to do wrong
25 525 525 ἐρωτάω 5 to ask
26 530 530 δείδω 5 to fear
27 535 535 παίω 5 to strike
28 540 540 ἀπᾴδω 5 to sing out of tune
29 544 544 συλλέγω 4 to collect
30 548 548 καλέω 4 to cal

In [76]:
import icu

icu_transliterator = icu.Transliterator.createInstance("Any-Latin")
value = "μῆνιν"
translit_value = icu_transliterator.transliterate(value)
print(translit_value)


AttributeError: module 'icu' has no attribute 'Transliterator'

In [30]:
i = 0
for foo in sorted(greeksentlens,key=greeksentlens.get):
    i = i + 1
    print(i,foo,len(greeksentlems[foo]),greeksentlems[foo])
    if(i>10):
        break

1 3668 2 ['φημί', '·']
2 158 3 ['οὗτος', 'λέγω', '·']
3 237 3 ['οὔτε', 'ἀποφεύγω', '·']
4 366 3 ['φημί', 'Ὀρόντας', '.']
5 681 3 ['ἀποκρίνω', 'Κλέαρχος', '·']
6 835 3 ['τίς', 'μένω', ';']
7 972 3 ['καί', 'λέγω', '·']
8 1099 3 ['τίς', 'κατάκειμαι', ';']
9 1264 3 ['ἀνατείνω', 'πᾶς', '.']
10 1280 3 ['δοκέω', 'οὗτος', '.']
11 1423 3 ['ἔξεστι', 'ὁράω', '·']


In [31]:
genabsolutes

['    <word id="8996241" form="Τισσαφέρνους" lemma="Τισσαφέρνης" postag="n-s---mg-" head="8996240" relation="SBJ"/>',
 '    <word id="8996572" form="Πισιδῶν" lemma="Πισίδης" postag="n-p---mg-" head="8996570" relation="SBJ"/>',
 '    <word id="8997865" form="οὐδενὸς" lemma="οὐδείς" postag="a-s---mg-" head="8997866" relation="SBJ"/>',
 '    <word id="8998522" form="ἐμοῦ" lemma="ἐγώ" postag="p-s---cg-" head="8998524" relation="SBJ"/>',
 '    <word id="8998604" form="τούτων" lemma="οὗτος" postag="a-p---mg-" head="8998603" relation="SBJ"/>',
 '    <word id="8998690" form="αὐτοῦ" lemma="αὐτός" postag="a-s---mg-" head="8998689" relation="SBJ"/>',
 '    <word id="8999054" form="Κύρου" lemma="Κῦρος" postag="n-s---mg-" head="8999055" relation="SBJ"/>',
 '    <word id="8999133" form="Κύρου" lemma="Κῦρος" postag="n-s---mg-" head="8999131" relation="SBJ"/>',
 '    <word id="9000182" form="πατρὸς" lemma="πατήρ" postag="n-s---mg-" head="9000180" relation="SBJ"/>',
 '    <word id="9000944" form="στενο

In [32]:
getfeats('9004803')

('n-s---mg-', 'Κῦρος', 'Κύρου', '9004802', 'SBJ')

In [33]:
formdict['9004803']

'    <word id="9004803" form="Κύρου" lemma="Κῦρος" postag="n-s---mg-" head="9004802" relation="SBJ"/>'

In [34]:
sorted(preplist)

['δίχα',
 'διά',
 'εἰς',
 'κατά',
 'μά',
 'μέχρι',
 'μετά',
 'μεταξύ',
 'νή',
 'πέρα',
 'πέραν',
 'παρά',
 'περί',
 'πλήν',
 'πλησίον',
 'πρό',
 'πρός',
 'σύν',
 'χωρίς',
 'ἀμφί',
 'ἀνά',
 'ἀντί',
 'ἀντίον',
 'ἀπό',
 'ἄνευ',
 'ἄχρι',
 'ἐκ',
 'ἐν',
 'ἐναντίον',
 'ἐντός',
 'ἐπέκεινα',
 'ἐπί',
 'ἔμπροσθεν',
 'ἕνεκα',
 'ἕως',
 'ὑπέρ',
 'ὑπό']

In [75]:
print(len(aobjverbs))
aolens = {}
for foo in aobjverbs:
    curlen = 0
    for boo in aobjverbs[foo]:
        curlen = curlen + aobjverbs[foo][boo]
    aolens[foo] = curlen
for foo in sorted(aolens,key=aolens.get,reverse=True):
    print(foo,aolens[foo],len(aobjverbs[foo]))

505
ποιέω 208 81
ἔχω 108 59
λέγω 90 35
οἶδα 81 47
πράσσω 71 29
ὁράω 67 52
κτάομαι 37 23
μανθάνω 29 14
παρέχω 26 25
νομίζω 23 17
λαμβάνω 23 17
διδάσκω 23 19
ἀκούω 23 12
ἐπίσταμαι 23 13
γιγνώσκω 20 17
φέρω 19 16
δίδωμι 18 15
εὑρίσκω 18 16
τιμάω 18 8
ὠφελέω 17 14
φιλέω 16 11
αἰσθάνομαι 16 15
τίθημι 15 9
πείθω 14 11
χράω 14 12
καλέω 14 13
πάσχω 14 8
παρασκευάζω 14 14
αἱρέω 13 12
βούλομαι 13 4
ἀγνοέω 12 8
ἡγέομαι 11 11
ἐρωτάω 11 6
καταμανθάνω 11 11
γράφω 10 9
ὑπομένω 10 9
ἄγω 10 8
σκοπέω 9 7
δύναμαι 9 8
διαλέγω 9 3
θεραπεύω 9 8
τρέφω 9 8
ἀποδείκνυμι 8 8
ἀποκτείνω 8 7
ἐπαινέω 8 8
ἀποκαλέω 8 8
ἀσκέω 8 7
ὠνέομαι 8 8
ἔρομαι 8 4
τάσσω 8 6
πορίζω 8 5
εὐεργετέω 8 5
μισέω 7 6
ἀφαιρέω 7 6
ἐπιδείκνυμι 7 7
μηχανάομαι 7 7
ἐσθίω 7 3
φοβέω 6 6
φυλάσσω 6 6
δοκέω 6 3
εὔχομαι 6 6
ἐμφύω 6 5
ἐπιμελέομαι 6 6
ἀποδίδωμι 6 3
ἐξετάζω 6 4
φροντίζω 5 3
ζητέω 5 5
διηγέομαι 5 4
ἐξηγέομαι 5 5
παύω 5 5
ἐργάζομαι 5 5
οἴομαι 5 4
προστίθημι 5 5
σῴζω 5 5
πλουτίζω 5 5
διατίθημι 5 5
σύμφημι 5 1
ἀδικέω 5 5
τρέπω 5 3
ἐπαείδω 5 

{'πείθω': {'Ἀθηναῖος': 1,
  'τις': 2,
  'ὅσος': 3,
  'πολύς': 1,
  'ἐκεῖνος': 1,
  'πόλις': 1,
  'ἄλλος': 1,
  'θεῖος': 1,
  'δέω': 1,
  'ἐγώ': 1,
  'σύ': 1},
 'γράφω': {'Σωκράτης': 1,
  'ὅς': 1,
  'βουλεύω': 1,
  'ὅσος': 1,
  'κρατέω': 1,
  'πεῖσα': 1,
  'αὐτός': 2,
  'δέλτα': 1,
  'γραφή': 1},
 'νομίζω': {'ὅς': 4,
  'θεός': 3,
  'μαντικός': 1,
  'τέχνη': 1,
  'Σωκράτης': 1,
  'οὗτος': 2,
  'σύ': 1,
  'κέρδος': 1,
  'χρῆμα': 1,
  'αὐτός': 1,
  'καλός': 1,
  'ὁ': 1,
  'ἀποστροφή': 1,
  'ἀνεπιστημοσύνη': 1,
  'μανθάνω': 1,
  'οἶδα': 1,
  'ἀνδρεία': 1},
 'εἰσφέρω': {'δαιμόνιον': 2, 'οὐδείς': 1},
 'διαφθείρω': {'νέος': 3},
 'οἶδα': {'ὄρνις': 1,
  'συμφέρω': 1,
  'ὅς': 10,
  'ἀνθρώπινος': 1,
  'ὅσος': 2,
  'ὁ': 2,
  'θεός': 1,
  'λέγω': 2,
  'Σωκράτης': 1,
  'δείκνυμι': 1,
  'δέω': 1,
  'ὁδός': 1,
  'οὗτος': 5,
  'χαίρω': 1,
  'ἱμάτιον': 1,
  'τάξις': 1,
  'ἄνανδρος': 1,
  'γεννάω': 1,
  'τίς': 1,
  'ἄνθρωπος': 1,
  'καλέω': 2,
  'πλῆθος': 1,
  'ἐπῳδή': 1,
  'τις': 7,
  'οὐδείς': 2,
  'ἀκο

In [36]:
i = 0
outf = open('wstem-pia.txt','w')
for form in formdict:
    if(not re.search('^1\.',citdict[form])):
        continue
    if( not re.search('lemma="[^"]+ω"',formdict[form])):
        continue
    
    if( not re.search('pia',formdict[form])):
        continue
    
    if(re.search('(άω|έω|όω)"',formdict[form])):
        continue
        
    
    curpostag,curlemma,curform,curhead,currel = getfeats(form)  
    if(not curlemma in lexicalentries):
        continue
    i = i + 1
    print(i,curpostag,citdict[form],lexicalentries[curlemma],curlemma,sep='\t',file=outf)
outf.close()

In [37]:
i = 0
tenses = {}
def addentry(curitem,curdict):
    if(curitem in curdict):
        curdict[curitem] = curdict[curitem] + 1
    else:
        curdict[curitem] = 1
        
outf = open('presimper.txt','w')
for foo in formdict:
    curcit = citdict[foo]
    if(not re.search('^1\.',curcit)):
        continue
    m = re.search('v..([fapi]ia)',formdict[foo])
    if(not m):
        continue
        
    curpostag,curlemma,curform,curhead,currel = getfeats(foo)  

    if(re.search('(έω|άω|όω)$',curlemma)):
        continue
    if(not re.search('(ω)$',curlemma)):
        continue
    addentry(m[1],tenses)
        
    if(curlemma in lexicalentries):
        curgloss = lexicalentries[curlemma]
    else:
        curgloss = 'nodef'
    i = i + 1
    print(i,curform,curcit,curlemma,curgloss,sep='\t',file=outf)
    
outf.close()

In [38]:
tenses

{'iia': 117, 'pia': 106, 'aia': 129, 'fia': 11}

In [39]:
len(tenses)

4

In [40]:
conditionals

{}

In [41]:
print(len(datmeansexamp))
datmeansexamp

320


[['αὐτῷ', 'ADV', 'ἦν', '8996316', '1.1.7'],
 ['ᾗ', 'ADV', 'ἐδύνατο', '8996847', '1.2.4'],
 ['πλοίοις', 'ADV', 'ἐζευγμένη', '8996903', '1.2.5'],
 ['Κύρῳ', 'ADV', 'ἦν', '8996966', '1.2.7'],
 ['μάχῃ', 'ADV', 'ἡττηθεὶς', '8997100', '1.2.9'],
 ['οἴνῳ', 'ADV', 'κεράσας', '8997387', '1.2.13'],
 ['ὑστεραίᾳ', 'ADV', 'ἧκεν', '8997816', '1.2.21'],
 ['τριήρεσι', 'ADV', 'καταδύσῃ', '8999108', '1.3.17'],
 ['τοῖς', 'ADV', 'ἦν', '8999325', '1.3.21'],
 ['αἷς', 'ADV', 'ἐπολιόρκει', '8999473', '1.4.2'],
 ['βίᾳ', 'ADV', 'παρελθεῖν', '8999609', '1.4.4'],
 ['τριήρεσι', 'ADV', 'διώκει', '8999804', '1.4.7'],
 ['ποσὶ', 'ADV', 'ἀπέσπα', '9000718', '1.5.3'],
 ['δρόμῳ', 'ADV', 'αἴρουσα', '9000719', '1.5.3'],
 ['πτέρυξιν', 'ADV', 'αἴρουσα', '9000723', '1.5.3'],
 ['κύκλῳ', 'ADV', 'περιερρεῖτο', '9000790', '1.5.4'],
 ['σχεδίαις', 'ADV', 'διαβαίνοντες', '9001180', '1.5.10'],
 ['ἡμέρᾳ', 'ADV', 'ἀφιππεύει', '9001281', '1.5.12'],
 ['ἀξίνῃ', 'ADV', 'ἵησι', '9001332', '1.5.12'],
 ['γένει', 'ADV', 'προσήκων', '9001629', '1

In [42]:
not []

True